# IMSNG_Rougine.ipynb
- Automatically Process the image data from GECKO facilities and search for transients in the subtracted images with `gpPy`
- Author: Gregory S.H. Paek (23.04.24)

## Library

In [1]:
from __future__ import print_function, division, absolute_import
import os, sys, glob, subprocess
import numpy as np
import astropy.io.ascii as ascii
import matplotlib.pyplot as plt
plt.ioff()
from astropy.nddata import CCDData
from preprocess import calib
from util import tool
from astropy.io import fits
from astropy.table import Table, vstack
from astropy import units as u
from ccdproc import ImageFileCollection
import warnings
warnings.filterwarnings(action='ignore')
# from itertools import product
from itertools import repeat
import multiprocessing
import time
start_localtime = time.strftime('%Y-%m-%d %H:%M:%S (%Z)', time.localtime())

In [2]:
#	plot setting
import matplotlib.pyplot as plt
import matplotlib as mpl
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "last_expr"

mpl.rcParams["axes.titlesize"] = 14
mpl.rcParams["axes.labelsize"] = 20
plt.rcParams['savefig.dpi'] = 500
plt.rc('font', family='serif')

## Ready

In [3]:
# try:
# 	obs = (sys.argv[1]).upper()
# except:
# 	obs = input(f"OBS TO PROCESS:").upper()

obs = 'LOAO'
print(f'# Observatory : {obs.upper()}')

try:
	ncores = int(sys.argv[2])
except:
	ncores = 8
print(f"- Number of Cores: {ncores}")

# Observatory : LOAO
- Number of Cores: 8


### Path

In [4]:
path_base = '/data4/gecko/factory'
path_ref = f'{path_base}/ref_frames/{obs.upper()}'
path_factory = f'{path_base}/{obs.lower()}'
path_save = f'/data6/bkgdata/{obs.upper()}'
path_log = f'/home/paek/log/{obs.lower()}.log'
path_keys = '/home/paek/table'
#------------------------------------------------------------
path_gal = '/data6/IMSNG/IMSNGgalaxies'
path_refcat = '/data4/gecko/factory/ref_frames/LOAO'
#------------------------------------------------------------
path_config = '/home/paek/config'
path_default_gphot = f'/home/paek/config/gphot.{obs.lower()}.config'
# path_mframe = f'{path_base}/master_frames'
path_mframe = f'/data3/paek/factory/master_frames'
path_calib = f'{path_base}/calib'
#------------------------------------------------------------
#	Codes
#------------------------------------------------------------
path_phot_sg = './phot/gregoryphot_2021.py'
path_phot_mp = './phot/gregoryphot_mp_2021.py'
path_phot_sub = './phot/gregoryphot_sub_2021.py'
path_find = './phot/gregoryfind_bulk_mp_2021.py'
#------------------------------------------------------------
if 'KCT_ASI1600MM' in obs:
	path_raw = '/data3/IMSNG/KCT/obsdata'
else:
	path_raw = f'/data6/obsdata/{obs.upper()}'
rawlist = sorted(glob.glob(path_raw+'/2*'))
#------------------------------------------------------------
path_obs = '/home/paek/table/obs.dat'
path_changehdr = '/home/paek/table/changehdr.dat'
path_alltarget = '/home/paek/table/alltarget.dat'
ccdinfo = tool.getccdinfo(obs, path_obs)

- Folder setting

In [5]:
if not os.path.exists(path_base):
	os.makedirs(path_base)
if not os.path.exists(path_ref):
	os.makedirs(path_ref)
if not os.path.exists(path_factory):
	os.makedirs(path_factory)
if not os.path.exists(path_save):
	os.makedirs(path_save)

### Table

In [6]:
logtbl = ascii.read(path_log)
datalist = np.copy(logtbl['date'])
obstbl = ascii.read(path_obs)
hdrtbl = ascii.read(path_changehdr)
alltbl = ascii.read(path_alltarget)
keytbl = ascii.read(f'{path_keys}/keys.dat')

## Process Summary Status

In [7]:
protbl = Table()
protbl['process'] = ['master_frame', 'pre_process', 'astrometry', 'cr_removal', 'defringe', 'photometry', 'image_stack', 'photometry_com', 'subtraction', 'photometry_sub', 'transient_search', 'total']
protbl['status'] = False
protbl['time'] = 0.0 * u.second

## Main Body

In [8]:
newlist = [i for i in rawlist if (i not in datalist) & (i+'/' not in datalist)]
if len(newlist) == 0:
	print('No new data')
	sys.exit()
else:
	print(newlist)

path = newlist[0]
# path = newlist[1]
tdict = dict()
starttime = time.time()
path_data = '{}/{}'.format(path_factory, os.path.basename(path))
#	Remove old folder and re-copy folder
rmcom = 'rm -rf {}'.format(path_data)
print(rmcom)
os.system(rmcom)
cpcom = 'cp -r {} {}'.format(path, path_data)
print(cpcom)
os.system(cpcom)

['/data6/obsdata/LOAO/2023_0422', '/data6/obsdata/LOAO/2023_0423']
rm -rf /data4/gecko/factory/loao/2023_0422
cp -r /data6/obsdata/LOAO/2023_0422 /data4/gecko/factory/loao/2023_0422


0

### Header Correction

In [9]:
ic0 = ImageFileCollection(path_data, keywords='*')
ic0.summary.write('{}/hdr.raw.dat'.format(path_data), format='ascii.tab', overwrite=True) 
#	Exceptions
#	DOAO CCD
if obs == 'DOAO':
	instrume = ic0.summary['instrume'][0]
	if instrume == 'Apogee USB/Net':obs = 'DOAO_APOGEE'
	elif instrume == '':			obs = 'DOAO_FLI'
	elif instrume == 'FLI':			obs = 'DOAO_FLI'
	elif instrume == 'Moravian C4-16000':		obs = 'DOAO_C416K'
else:
	pass
obsinfo = calib.getobsinfo(obs, obstbl)
if obs == 'SAO_C361K':
	xbinning = ic0.summary['xbinning'][0]
	if xbinning > 1:
		print(f'{obs} : BINNINGx{xbinning}')
		obsinfo['pixscale'] = obsinfo['pixscale']*xbinning
	if ic0.summary['instrume'][0] == 'ASCOM Camera Driver for FLI Kepler':
		obsinfo['pixscale'] = 0.311
		obsinfo['fov'] = 0.25*60.
		obsinfo['gain'] = float(ic0.summary['egain'][0])
#	KHAO Binning
if obs == 'KHAO':
	xbinning = ic0.summary['xbinning'][0]
	if xbinning > 1:
		obsinfo['pixscale'] = obsinfo['pixscale']*2
#	LOAO
if obs == 'LOAO':
	instrume = ic0.summary['instrume'][0]
	if 'Finger Lakes' in instrume:
		obs = 'LOAO_FLI'
		obsinfo = calib.getobsinfo(obs, obstbl)
#	RASA Mode
if obs == 'RASA36':
	if 'hdr' in path:
		mode = 'hdr'
		badmode = True
	elif 'high' in path:
		mode = 'high'
		badmode = True
	else:
		mode = 'high'
		badmode = True
		pass
	print(f'Master Frame Mode:{mode} [Bad Mode:{badmode}]')

calib.correcthdr_routine(path_data, hdrtbl, obs)
print("Correction Done")
# objfilterlist, objexptimelist, flatfilterlist, darkexptimelist, obstime = calib.correcthdr_routine(path_data, hdrtbl)
ic1 = ImageFileCollection(path_data, keywords='*')
ic1.summary.write('{}/hdr.cor.dat'.format(path_data), format='ascii.tab', overwrite=True)
try:
	nobj = len(ic1.filter(imagetyp='OBJECT').summary)
except:
	nobj = len(ic1.filter(imagetyp='object').summary)	

------------------------------------------------------------
CHANGE TO UNIVERSAL HEADER SERIES ...
------------------------------------------------------------

/data4/gecko/factory/loao/2023_0422/dark.2x2.200.20230422.0011.fits
/data4/gecko/factory/loao/2023_0422/dark.2x2.200.20230422.0012.fits
/data4/gecko/factory/loao/2023_0422/dark.2x2.200.20230422.0013.fits
/data4/gecko/factory/loao/2023_0422/dark.2x2.200.20230422.0014.fits
/data4/gecko/factory/loao/2023_0422/dark.2x2.200.20230422.0015.fits
/data4/gecko/factory/loao/2023_0422/dark.2x2.200.20230423.0016.fits
/data4/gecko/factory/loao/2023_0422/dark.2x2.200.20230423.0017.fits
/data4/gecko/factory/loao/2023_0422/dark.2x2.200.20230423.0018.fits
/data4/gecko/factory/loao/2023_0422/dark.2x2.200.20230423.0019.fits
/data4/gecko/factory/loao/2023_0422/dark.2x2.200.20230423.0020.fits
/data4/gecko/factory/loao/2023_0422/dark.2x2.200.20230423.1055.fits
/data4/gecko/factory/loao/2023_0422/dark.2x2.200.20230423.1056.fits
/data4/gecko/factory/lo

### Marking the `GECKO` data

In [10]:
# testobj = 'S190425z'
project = "IMSNG"
obsmode = "MONITORING" # Default
for obj in ic1.filter(imagetyp='object').summary['object']:
	if 'MS' in obj[:2]: # MS230425 (test event)
		print(obj)
		project = "GECKO"
		obsmode = "TEST"
	elif 'S2' in obj[:2]: # S230425 (super event)
		print(obj)
		project = "GECKO"
		obsmode = "FOLLOWUP" # Follow-up
	else:
		pass
print(f"[{project}] {obsmode}")

[IMSNG] MONITORING


- Slack notification

In [11]:
OAuth_Token = keytbl['key'][keytbl['name']=='slack'].item()

channel = '#pipeline'
text = f'[`gpPy`/{project}-{obsmode}] Start Processing {obs} {os.path.basename(path)} Data ({nobj} objects) with {ncores} cores'

param_slack = dict(
	token = OAuth_Token,
	channel = channel,
	text = text,
)

tool.slack_bot(**param_slack)

<Response [200]>


### Master Frame

- Bias

In [12]:
st = time.time()
#------------------------------------------------------------
#	BIAS
#------------------------------------------------------------
try:
	biasnumb = len(ic1.filter(imagetyp='Bias').summary)
except:
	biasnumb = 0
# if len(ic1.filter(imagetyp='Bias').summary) != 0:
if biasnumb != 0:
	mzero = calib.master_zero(ic1, fig=False)
	# print(zeroim)
	date = fits.getheader(f'{path_data}/zero.fits')['date-obs'][:10].replace('-', '')
	if obs == 'RASA36':
		zeroim = f'{path_mframe}/{obs}/zero/{date}-zero_{mode}.fits'
	else:
		zeroim = f'{path_mframe}/{obs}/zero/{date}-zero.fits'
	cpcom = f'cp {path_data}/zero.fits {zeroim}'
	print(cpcom)
	os.system(cpcom)
	plt.close('all')
else:
	#	IF THERE IS NO FLAT FRAMES, BORROW FROM CLOSEST OTHER DATE
	print('\nNO BIAS FRAMES\n')
	if obs == 'RASA36':
		pastzero = np.array(glob.glob(f'{path_mframe}/{obs}/zero/*zero_{mode}.fits'))
	else:
		pastzero = np.array(glob.glob(f'{path_mframe}/{obs}/zero/*zero.fits'))
	#	CALCULATE CLOSEST ONE FROM TIME DIFFERENCE
	deltime = []
	for date in pastzero:
		zeromjd = calib.isot_to_mjd((os.path.basename(date)).split('-')[0])
		deltime.append(np.abs(ic1.summary['mjd'][0]-zeromjd))
	indx_closet = np.where(deltime == np.min(deltime))
	# tmpzero = path_data+'/'+os.path.basename(np.asscalar(pastzero[indx_closet]))
	tmpzero = f"{path_data}/{os.path.basename(pastzero[indx_closet][0])}"
	# cpcom = 'cp {} {}'.format(np.asscalar(pastzero[indx_closet]), tmpzero)
	cpcom = f'cp {pastzero[indx_closet][0]} {tmpzero}'
	print(cpcom)
	os.system(cpcom)
	# if obs != 'KCT':
	if 'KCT_ASI1600MM' in obs:
		#KCT Exception
		mzero = CCDData.read(tmpzero, hdu=0, unit='adu')
	elif obs == 'RASA36':
		if (mode == 'high') & (badmode == True):
			mzero = CCDData.read(tmpzero, hdu=0).multiply(20)
			print('[Bad mode] Multiply 20 on the high mode bias.')
		else:
			mzero = CCDData.read(tmpzero, hdu=0)
	elif obs == 'LSGT':
		mzero = CCDData.read(tmpzero, hdu=0, unit='adu')
	else:
		mzero = CCDData.read(tmpzero, hdu=0)#, unit='adu')
	mzero.meta['FILENAME'] = os.path.basename(tmpzero)

------------------------------------------------------------
MAKING MASTER ZERO
------------------------------------------------------------

20 ZERO IMAGES WILL BE COMBINED.
cp /data4/gecko/factory/loao/2023_0422/zero.fits /data3/paek/factory/master_frames/LOAO/zero/20230423-zero.fits


cp: cannot create regular file ‘/data3/paek/factory/master_frames/LOAO/zero/20230423-zero.fits’: Permission denied


- Dark

In [13]:
#------------------------------------------------------------
#	DARK (ITERATION FOR EACH EXPOSURE TIMES)
#------------------------------------------------------------
try:
	darkexptimelist = sorted(list(set(ic1.filter(imagetyp='dark').summary['exptime'])))
	darknumb = len(darkexptimelist)
except:
	darknumb = 0
darkdict = dict()
# if len(darkexptimelist) != 0:
if darknumb != 0:
	dark_process = True
	for i, exptime in enumerate(darkexptimelist):
		print('PRE PROCESS FOR DARK ({} sec)\t[{}/{}]'.format(exptime, i+1, len(darkexptimelist)))
		mdark = calib.master_dark(ic1, mzero=mzero, exptime=exptime, fig=False)
		darkdict['{}'.format(int(exptime))] = mdark

		date = fits.getheader(f'{path_data}/dark-{int(exptime)}.fits')['date-obs'][:10].replace('-', '')
		if obs == 'RASA36':
			darkim = f'{path_mframe}/{obs}/dark/{int(exptime)}-{date}-dark_{mode}.fits'
		else:
			darkim = f'{path_mframe}/{obs}/dark/{int(exptime)}-{date}-dark.fits'
		# print(zeroim)
		cpcom = 'cp {}/dark-{}.fits {}'.format(path_data, int(exptime), darkim)
		print(cpcom)
		os.system(cpcom)
		plt.close('all')
else:
	#	Borrow
	print('\nNO DARK FRAMES\n')
	objexptimelist = sorted(list(set(ic1.filter(imagetyp='object').summary['exptime'])))
	exptime = objexptimelist[-1]
	# pastdark = np.array(glob.glob('{}/{}/dark/{}*dark*.fits'.format(path_mframe, obs, int(exptime))))
	if obs == 'RASA36':
		pastdark = np.array(glob.glob(f'{path_mframe}/{obs}/dark/{int(exptime)}*dark_{mode}.fits'))
	else:
		pastdark = np.array(glob.glob(f'{path_mframe}/{obs}/dark/{int(exptime)}*dark.fits'))

	if len(pastdark) == 0:
		pastdark = np.array(glob.glob('{}/{}/dark/*dark*.fits'.format(path_mframe, obs)))
	else:
		pass
	#	CALCULATE CLOSEST ONE FROM TIME DIFFERENCE
	deltime = []
	delexptime = []
	darkexptimes = []
	for date in pastdark:
		# darkmjd = calib.isot_to_mjd((os.path.basename(date)).split('-')[0])
		darkmjd = calib.isot_to_mjd((os.path.basename(date)).split('-')[1])
		darkexptime = int( os.path.basename(date).split('-')[0] )
		# darkexptime = delexptime.append(int( os.path.basename(date).split('-')[1] ))
		darkexptimes.append(darkexptime)
		deltime.append(np.abs(ic1.summary['mjd'][0]-darkmjd))
	if 'KCT' in obs:
		indx_closet = np.where(
			(np.abs(np.array(darkexptimes)-exptime) == np.min(np.abs(np.array(darkexptimes)-exptime)))
		)
	else:
		indx_closet = np.where(
			(deltime == np.min(deltime)) &
			(darkexptimes == np.max(darkexptimes))
		)
	if len(indx_closet[0]) == 0:
		indx_closet = np.where(
			(deltime == np.min(deltime))
		)
	else:
		pass
	# tmpdark = path_data+'/'+os.path.basename(pastdark[indx_closet].item())
	# tmpdark = '{}/{}'.format(path_data, os.path.basename(pastdark[indx_closet[0]].item()))
	# tmpdark = pastdark[indx_closet[0]].item()
	tmpdark = pastdark[indx_closet][-1]
	exptime = int(fits.getheader(tmpdark)['exptime'])

	# cpcom = 'cp {} {}/dark-{}.fits'.format(tmpdark, path_data, int(exptime))
	cpcom = 'cp {} {}'.format(tmpdark, path_data, int(exptime))
	print(cpcom)
	os.system(cpcom)
	if 'KCT' in obs:
		#KCT Exception
		mdark = CCDData.read(tmpdark, hdu=0, unit='adu')
	elif obs == 'RASA36':
		if (mode == 'high') & (badmode == True):
			mdark = CCDData.read(tmpdark, hdu=0).multiply(20)
			print('[Bad mode] Multiply 20 on the high mode dark.')
		else:
			mdark = CCDData.read(tmpdark, hdu=0)
	elif obs == 'LSGT':
		mdark = CCDData.read(tmpdark, hdu=0, unit='adu')
	else:
		mdark = CCDData.read(tmpdark, hdu=0)#, unit='adu')
	mdark.meta['FILENAME'] = os.path.basename(tmpdark)
	mdark.meta['EXPTIME'] = exptime
	darkdict['{}'.format(int(exptime))] = mdark

PRE PROCESS FOR DARK (200.0 sec)	[1/1]
------------------------------------------------------------
MAKING MASTER DARK
------------------------------------------------------------

cp /data4/gecko/factory/loao/2023_0422/dark-200.fits /data3/paek/factory/master_frames/LOAO/dark/200-20230423-dark.fits


cp: cannot create regular file ‘/data3/paek/factory/master_frames/LOAO/dark/200-20230423-dark.fits’: Permission denied


- Flat

In [14]:
flatdict = dict()
try:
	flatfilterlist = list(set(ic1.filter(imagetyp='flat').summary['filter']))
	for i, filte in enumerate(flatfilterlist):
		# print(i, filte)
		print('MAKING MASTER FLAT IN {}-BAND'.format(filte))
		mflat = calib.master_flat(ic1, mzero, filte, mdark=mdark, fig=True)
		flatdict[filte] = mflat

		date = fits.getheader(f'{path_data}/dark-{int(exptime)}.fits')['date-obs'][:10].replace('-', '')
		if obs == 'RASA36':
			flatim = f'{path_mframe}/{obs}/flat/{date}-n{filte}_{mode}.fits'
		else:
			flatim = f'{path_mframe}/{obs}/flat/{date}-n{filte}.fits'
		cpcom = f'cp {path_data}/n{filte}.fits {flatim}'
		print(cpcom)
		os.system(cpcom)
		plt.close('all')
except:
	print('No flat calibration image.')
	# flatdict['None'] = None
	pass
# tdict['masterframe'] = time.time() - st
protbl['status'][protbl['process']=='master_frame'] = True
protbl['time'][protbl['process']=='master_frame'] = int(time.time() - st)
#------------------------------------------------------------
#	OBJECT CALIBARTION (ZERO, DARK, FLAT)
#------------------------------------------------------------
st_ = time.time()
comment     = '='*60+'\n' \
			+ 'OBJECT CALIBRATION\n' \
			+ '='*60+'\n'
print(comment)
objfilterlist = sorted(list(set(ic1.filter(imagetyp='object').summary['filter'])))
objexptimelist = sorted(list(set(ic1.filter(imagetyp='object').summary['exptime'])))
for i, filte in enumerate(objfilterlist):
	print('PRE PROCESS FOR {} FILTER OBJECT\t[{}/{}]'.format(filte, i+1, len(objfilterlist)))
	if filte in flatdict.keys():
		mflat = flatdict[filte]
	else:
		print('\nNO {} FLAT FRAMES\n'.format(filte))
		#	CALCULATE CLOSEST ONE FROM TIME DIFFERENCE
		deltime = []
		if obs != 'RASA36':
			pastflat = np.array(glob.glob('{}/{}/flat/*n{}*.fits'.format(path_mframe, obs, filte)))
			for date in pastflat:
				flatmjd = calib.isot_to_mjd((os.path.basename(date)).split('-')[0])
				deltime.append(np.abs(ic1.summary['mjd'][0]-flatmjd))
		elif obs == 'RASA36':
			pastflat = np.array(glob.glob(f'{path_mframe}/{obs}/flat/*_{mode}-n{filte}*.fits'))
			for date in pastflat:
				flatmjd = fits.getheader(date)['MJD']
				deltime.append(np.abs(ic1.summary['mjd'][0]-flatmjd))

		indx_closet = np.where(deltime == np.min(deltime))
		tmpflat = '{}/{}'.format(path_data, os.path.basename(pastflat[indx_closet][0].item()))
		# tmpflat = pastflat[indx_closet][0].item()
		cpcom = 'cp {} {}'.format(pastflat[indx_closet][0].item(), tmpflat)
		print(cpcom)
		os.system(cpcom)
		if ('KCT' not in obs) & (obs != 'LSGT'):
			mflat = CCDData.read(tmpflat, hdu=0)#, unit='adu')
		elif obs == 'LSGT':
			mflat = CCDData.read(tmpflat, hdu=0, unit='adu')
		else:
			#KCT Exception
			mflat = CCDData.read(tmpflat, hdu=0, unit='adu')
			mflat.meta['FILENAME'] = os.path.basename(tmpflat)
		mflat.meta['FILENAME'] = os.path.basename(tmpflat)
		flatdict[filte] = mflat
	for expt in objexptimelist:
		if str(int(expt)) in darkdict.keys():
			mdark = darkdict[str(int(expt))]
		else:
			mdark = darkdict[list(darkdict.keys())[-1]]
		calib.calibration(ic1, mzero, mflat, filte, mdark=mdark)
# tdict['objectcorrection'] = time.time() - st - tdict[list(tdict.keys())[-1]]
protbl['status'][protbl['process']=='pre_process'] = True
protbl['time'][protbl['process']=='pre_process'] = int(time.time() - st_)
#	Corrected image list
fzimlist = []
for ims in ('{}/fz*.fits'.format(path_data), '{}/fz*.fit'.format(path_data), '{}/fz*.fts'.format(path_data)):
	fzimlist.extend(sorted(glob.glob(ims)))

MAKING MASTER FLAT IN R-BAND
------------------------------------------------------------
MAKING MASTER FLAT
------------------------------------------------------------

SUBTRACT MASTER ZERO & DARK FROM R FLAT
5 R FLAT IMAGES WILL BE COMBINED.
cp /data4/gecko/factory/loao/2023_0422/nR.fits /data3/paek/factory/master_frames/LOAO/flat/20230423-nR.fits
MAKING MASTER FLAT IN V-BAND
------------------------------------------------------------
MAKING MASTER FLAT
------------------------------------------------------------

SUBTRACT MASTER ZERO & DARK FROM V FLAT


cp: cannot create regular file ‘/data3/paek/factory/master_frames/LOAO/flat/20230423-nR.fits’: Permission denied


5 V FLAT IMAGES WILL BE COMBINED.
cp /data4/gecko/factory/loao/2023_0422/nV.fits /data3/paek/factory/master_frames/LOAO/flat/20230423-nV.fits
MAKING MASTER FLAT IN I-BAND
------------------------------------------------------------
MAKING MASTER FLAT
------------------------------------------------------------

SUBTRACT MASTER ZERO & DARK FROM I FLAT


cp: cannot create regular file ‘/data3/paek/factory/master_frames/LOAO/flat/20230423-nV.fits’: Permission denied


9 I FLAT IMAGES WILL BE COMBINED.
cp /data4/gecko/factory/loao/2023_0422/nI.fits /data3/paek/factory/master_frames/LOAO/flat/20230423-nI.fits
MAKING MASTER FLAT IN B-BAND
------------------------------------------------------------
MAKING MASTER FLAT
------------------------------------------------------------

SUBTRACT MASTER ZERO & DARK FROM B FLAT


cp: cannot create regular file ‘/data3/paek/factory/master_frames/LOAO/flat/20230423-nI.fits’: Permission denied


5 B FLAT IMAGES WILL BE COMBINED.
cp /data4/gecko/factory/loao/2023_0422/nB.fits /data3/paek/factory/master_frames/LOAO/flat/20230423-nB.fits
OBJECT CALIBRATION



cp: cannot create regular file ‘/data3/paek/factory/master_frames/LOAO/flat/20230423-nB.fits’: Permission denied


PRE PROCESS FOR B FILTER OBJECT	[1/2]
------------------------------------------------------------
OBJECT CORRECTION
------------------------------------------------------------

PRE PROCESS FOR R FILTER OBJECT	[2/2]
------------------------------------------------------------
OBJECT CORRECTION
------------------------------------------------------------



### WCS Calculation

In [15]:
#------------------------------------------------------------
#	ASTROMETRY
#------------------------------------------------------------
st_ = time.time()
print('ASTROMETRY START')
print('='*60)
astrometryfailist = []
# fzimlist = sorted(glob.glob(path_data+'/fz*.fits'))
astimlist = []
astotlist = []
astralist = []
astdelist = []

for inim in fzimlist:
	obj = (fits.getheader(inim)['object']).upper()
	if (obj in alltbl['obj']):
		indx_target = np.where(obj == alltbl['obj'])[0][0]
		ra, dec = alltbl['ra'][indx_target].item(), alltbl['dec'][indx_target].item()
		astimlist.append(inim)
		astralist.append(ra)
		astdelist.append(dec)
	else:
		astotlist.append(inim)
#	Astrometry (IMSNG field)
if __name__ == '__main__':
	with multiprocessing.Pool(processes=ncores) as pool:
		results = pool.starmap(calib.astrometry, zip(astimlist, repeat(obsinfo['pixscale']), astralist, astdelist, repeat(obsinfo['fov']/60.), repeat(15)))
#	Astrometry (non IMSNG field)
if __name__ == '__main__':
	with multiprocessing.Pool(processes=ncores) as pool:
		results = pool.starmap(calib.astrometry, zip(astotlist, repeat(obsinfo['pixscale']), repeat(None), repeat(None), repeat(None), repeat(60)))
#	Astrometry (failed IMSNG field)
astfailist = []
for inim in astimlist:
	if (os.path.exists('{}/a{}'.format(path_data, os.path.basename(inim))) == False):
		astfailist.append(inim)
if __name__ == '__main__':
	with multiprocessing.Pool(processes=ncores) as pool:
		results = pool.starmap(calib.astrometry, zip(astfailist, repeat(obsinfo['pixscale']), repeat(None), repeat(None), repeat(None), repeat(60)))
for inim in astfailist:
	if (os.path.exists('{}/a{}'.format(path_data, os.path.basename(inim))) == False):
		astrometryfailist.append('{}/a{}'.format(path_data, os.path.basename(inim)))

os.system('rm '+path_data+'/*.axy '+path_data+'/*.corr '+path_data+'/*.xyls '+path_data+'/*.match '+path_data+'/*.rdls '+path_data+'/*.solved '+path_data+'/*.wcs ')
print('ASTROMETRY COMPLETE\n'+'='*60)
# tdict['astronomy'] = time.time() - st - tdict[list(tdict.keys())[-1]]
protbl['status'][protbl['process']=='astrometry'] = True
protbl['time'][protbl['process']=='astrometry'] = int(time.time() - st_)

ASTROMETRY START
/usr/local/astrometry/bin/solve-field /data4/gecko/factory/loao/2023_0422/fzobj.NGC5850.20230423.1009.fits --scale-unit arcsecperpix --scale-low 0.7146 --scale-high 0.8734000000000001 --no-plots --new-fits /data4/gecko/factory/loao/2023_0422/afzobj.NGC5850.20230423.1009.fits --overwrite --use-sextractor --cpulimit 15 --ra 15:07:07.644 --dec +01:32:40.74 --radius 0.4683333333333334/usr/local/astrometry/bin/solve-field /data4/gecko/factory/loao/2023_0422/fzobj.NGC6070.20230423.1021.fits --scale-unit arcsecperpix --scale-low 0.7146 --scale-high 0.8734000000000001 --no-plots --new-fits /data4/gecko/factory/loao/2023_0422/afzobj.NGC6070.20230423.1021.fits --overwrite --use-sextractor --cpulimit 15 --ra 16:09:58.680 --dec +00:42:34.31 --radius 0.4683333333333334/usr/local/astrometry/bin/solve-field /data4/gecko/factory/loao/2023_0422/fzobj.NGC5850.20230423.1013.fits --scale-unit arcsecperpix --scale-low 0.7146 --scale-high 0.8734000000000001 --no-plots --new-fits /data4/geck


> WARNING: default.sex not found, using internal defaults

> 
----- SExtractor 2.19.5 started on 2023-04-26 at 10:44:21 with 1 thread

> Setting catalog parameters

> WARNING: default.sex not found, using internal defaults


> WARNING: default.sex not found, using internal defaults

> Reading detection filter

> WARNING: default.sex not found, using internal defaults

> Initializing catalog
> 
----- SExtractor 2.19.5 started on 2023-04-26 at 10:44:21 with 1 thread

> 
----- SExtractor 2.19.5 started on 2023-04-26 at 10:44:21 with 1 thread

> Setting catalog parameters
> 
----- SExtractor 2.19.5 started on 2023-04-26 at 10:44:21 with 1 thread

> Setting catalog parameters
> Setting catalog parameters

> WARNING: default.sex not found, using internal defaults

> Reading detection filter
> Reading detection filter
> Reading detection filter
> Initializing catalog
> Initializing catalog
> Initializing catalog
> Looking for fzobj.NGC6070.20230423.1023.fits
> 
----- SExtractor 2.19.5 starte

Sorting brightness using MAG_AUTO and BACKGROUND columns failed; falling back to MAG_AUTO.
Reading sort column "MAG_AUTO"
Sorting sort column
mmapping input file
Copying table header.
Writing row 0
Done
Sorting brightness using MAG_AUTO and BACKGROUND columns failed; falling back to MAG_AUTO.
Reading sort column "MAG_AUTO"
Sorting sort column
mmapping input file
Copying table header.
Writing row 0
Done
Sorting brightness using MAG_AUTO and BACKGROUND columns failed; falling back to MAG_AUTO.
Reading sort column "MAG_AUTO"
Sorting sort column
mmapping input file
Copying table header.
Writing row 0
Done
Sorting brightness using MAG_AUTO and BACKGROUND columns failed; falling back to MAG_AUTO.
Sorting brightness using MAG_AUTO and BACKGROUND columns failed; falling back to MAG_AUTO.
Reading sort column "MAG_AUTO"
Sorting sort column
mmapping input file
Copying table header.
Writing row 0
Done
Reading sort column "MAG_AUTO"
Sorting sort column
mmapping input file
Copying table header.
Writ


> WARNING: default.sex not found, using internal defaults

> 
----- SExtractor 2.19.5 started on 2023-04-26 at 10:44:25 with 1 thread

> Setting catalog parameters
> Reading detection filter
> Initializing catalog
> Looking for fzobj.NGC5850.20230423.1014.fits
----- Measuring from: fzobj.NGC5850.20230423.1014.fits [0/3]
      "NGC5850" / no ext. header / 2048x2048 / 64 bits (floats)
Detection+Measurement image: > Setting up background maps

> WARNING: default.sex not found, using internal defaults

> 
----- SExtractor 2.19.5 started on 2023-04-26 at 10:44:25 with 1 thread

> Setting catalog parameters
> Reading detection filter
> Initializing catalog
> Looking for fzobj.NGC5962.20230423.1020.fits
> Setting up background map at line:   64
----- Measuring from: fzobj.NGC5962.20230423.1020.fits [0/3]
      "NGC5962" / no ext. header / 2048x2048 / 64 bits (floats)
Detection+Measurement image: > Setting up background maps
> Setting up background map at line:  128
> Setting up background ma

  log-odds ratio 53.9172 (2.60593e+23), 7 match, 0 conflict, 26 distractors, 11 index.
  RA,Dec = (234.131,16.6063), pixel scale 0.794445 arcsec/pix.
  Hit/miss:   Hit/miss: --+-----++-+---+----+-----------+(best)-------------------------------------------------------------------
Field 1 did not solve (index index-4208.fits, field objects 11-20).
  log-odds ratio 54.7055 (5.7316e+23), 7 match, 0 conflict, 26 distractors, 11 index.
  RA,Dec = (234.132,16.6067), pixel scale 0.794422 arcsec/pix.
  Hit/miss:   Hit/miss: --+-----++++--------+-----------+(best)-------------------------------------------------------------------
Field 1 did not solve (index index-4208.fits, field objects 11-20).
Field 1 did not solve (index index-4208.fits, field objects 11-20).
Field 1 did not solve (index index-4207-07.fits, field objects 11-20).
Field 1: solved with index index-4207-02.fits.
Field 1 solved: writing to file /data4/gecko/factory/loao/2023_0422/fzobj.NGC5962.20230423.1017.solved to indicate th

...

Field 1 did not solve (index index-4208.fits, field objects 21-30).
Field 1 did not solve (index index-4207-03.fits, field objects 21-30).
  log-odds ratio 237.023 (8.66454e+102), 32 match, 1 conflict, 106 distractors, 36 index.
  RA,Dec = (308.715,60.1528), pixel scale 0.794789 arcsec/pix.
  Hit/miss:   Hit/miss: -++++-++-++----++++---++c++-+--+-++-----++-+-+--++-+------+-------+-------+-----------------------+-
Field 1: solved with index index-4206-03.fits.
Field 1 solved: writing to file /data4/gecko/factory/loao/2023_0422/fzobj.NGC6946.20230423.1044.solved to indicate this.


> Line:  900  Objects:     7727 detected /     2154 sextracted
> Line:  675  Objects:     5417 detected /      571 sextracted
> Line:  700  Objects:     5620 detected /      712 sextracted
> Line:  925  Objects:     7962 detected /     2305 sextracted
> Line:  725  Objects:     5825 detected /      843 sextracted
> Line:  950  Objects:     8170 detected /     2458 sextracted
> Line:  750  Objects:     6038 detected /      984 sextracted
> Line:  975  Objects:     8374 detected /     2592 sextracted
> Line:  775  Objects:     6229 detected /     1115 sextracted
> Line: 1000  Objects:     8623 detected /     2753 sextracted
> Line:  800  Objects:     6411 detected /     1248 sextracted
> Line:  825  Objects:     6591 detected /     1382 sextracted
> Line: 1025  Objects:     8836 detected /     2902 sextracted
> Line:  850  Objects:     6811 detected /     1526 sextracted
> Line: 1050  Objects:     9022 detected /     3026 sextracted
> Line:  875  Objects:     7021 detected /     1666 sex

Field: /data4/gecko/factory/loao/2023_0422/fzobj.NGC6946.20230423.1044.fits
Field center: (RA,Dec) = (308.715441, 60.152657) deg.
Field center: (RA H:M:S, Dec D:M:S) = (20:34:51.706, +60:09:09.565).
Field size: 27.1201 x 27.1195 arcminutes
Field rotation angle: up is -175.862 degrees E of N
Field parity: pos
Creating new FITS file "/data4/gecko/factory/loao/2023_0422/afzobj.NGC6946.20230423.1044.fits"...



> Line: 1075  Objects:     9028 detected /     2903 sextracted
> Line: 1300  Objects:    11145 detected /     4518 sextracted
> Line: 1100  Objects:     9265 detected /     3049 sextracted
> Line: 1325  Objects:    11357 detected /     4677 sextracted
> Line: 1125  Objects:     9511 detected /     3207 sextracted
> Line: 1350  Objects:    11555 detected /     4808 sextracted
> Line: 1150  Objects:     9706 detected /     3337 sextracted
> Line: 1375  Objects:    11766 detected /     4943 sextracted
> Line: 1175  Objects:     9951 detected /     3487 sextracted
> Line: 1400  Objects:    11981 detected /     5084 sextracted
> Line: 1200  Objects:    10151 detected /     3614 sextracted
> Line: 1425  Objects:    12191 detected /     5223 sextracted
> Line: 1225  Objects:    10356 detected /     3756 sextracted
> Line: 1450  Objects:    12373 detected /     5345 sextracted
> Line: 1250  Objects:    10572 detected /     3896 sextracted
> Line: 1475  Objects:    12574 detected /     5483 sex

Sorting brightness using MAG_AUTO and BACKGROUND columns failed; falling back to MAG_AUTO.
Reading sort column "MAG_AUTO"
Sorting sort column
mmapping input file
Copying table header.
Writing row 0
Done
Sorting brightness using MAG_AUTO and BACKGROUND columns failed; falling back to MAG_AUTO.
Reading sort column "MAG_AUTO"
Sorting sort column
mmapping input file
Copying table header.
Writing row 0
Done
Solving...
Solving...
Reading file "/data4/gecko/factory/loao/2023_0422/fzobj.NGC6946.20230423.1040.axy"...
Only searching for solutions within 0.468333 degrees of RA,Dec (308.718,60.1539)
Field 1 did not solve (index index-4209.fits, field objects 1-10).
Field 1 did not solve (index index-4208.fits, field objects 1-10).
Field 1 did not solve (index index-4207-03.fits, field objects 1-10).
Field 1 did not solve (index index-4206-03.fits, field objects 1-10).
Field 1 did not solve (index index-4205-03.fits, field objects 1-10).
Field 1 did not solve (index index-4204-15.fits, field object

### Cosmic-ray Removal

In [16]:
st_ = time.time()
print('Quick seeing measurement with SE & Cosmic ray removal')
print('='*60)
gain = ccdinfo['gain'].value
rdnoise = ccdinfo['rdnoise']

# afzimlist = sorted(glob.glob(path_data+'/afz*.fits'))
afzimlist = []
for ims in ('{}/a*.fits'.format(path_data), '{}/a*.fit'.format(path_data), '{}/a*.fts'.format(path_data)):
	afzimlist.extend(sorted(glob.glob(ims)))
outimlist = []
for i, inim in enumerate(afzimlist):
	outim = '{}/cr{}'.format(os.path.dirname(inim), os.path.basename(inim))
	outimlist.append(outim)
if ('KCT' not in obs) & ('RASA36' not in obs) & ('LOAO_FLI' not in obs):
	#	Seeing measurement
	if __name__ == '__main__':
		with multiprocessing.Pool(processes=ncores) as pool:
			results = pool.starmap(tool.SE_seeing, zip(afzimlist, repeat(obs), repeat(path_obs), repeat(path_config), repeat(3*u.arcsecond), repeat(0.95), repeat(True)))
	#	Remove cosmic-ray
	if __name__ == '__main__':
		with multiprocessing.Pool(processes=ncores) as pool:
			results = pool.starmap(calib.cr_removal, zip(afzimlist, outimlist, repeat(gain), repeat(rdnoise)))
else:
	print('Skip Seeing measurement & CR remove processes for {}'.format(obs))
	for inim, outim in zip(afzimlist, outimlist):
		cpcom = 'cp {} {}'.format(inim, outim)
		print(cpcom)
		os.system(cpcom)
protbl['status'][protbl['process']=='cr_removal'] = True
protbl['time'][protbl['process']=='cr_removal'] = int(time.time() - st_)

Quick seeing measurement with SE & Cosmic ray removal


> 
----- SExtractor 2.19.5 started on 2023-04-26 at 10:44:49 with 1 thread

> Setting catalog parameters
> 
----- SExtractor 2.19.5 started on 2023-04-26 at 10:44:49 with 1 thread

> Setting catalog parameters
> 
----- SExtractor 2.19.5 started on 2023-04-26 at 10:44:49 with 1 thread

> Setting catalog parameters
> 
----- SExtractor 2.19.5 started on 2023-04-26 at 10:44:49 with 1 thread

> Reading detection filter
> Setting catalog parameters
> Initializing Neural Network
> Reading Neural Network Weights
> Reading detection filter
> Initializing Neural Network
> Reading Neural Network Weights
> 
----- SExtractor 2.19.5 started on 2023-04-26 at 10:44:49 with 1 thread

> Reading detection filter
> Setting catalog parameters
> Initializing catalog
> Initializing Neural Network
> Reading Neural Network Weights
> Reading detection filter
> Initializing Neural Network
> Reading Neural Network Weights
> Initializing catalog
> Reading detection filter
> Looking for afzobj.NGC5850.20230423.1011

Remove 783 cosmic-ray for /data4/gecko/factory/loao/2023_0422/afzobj.NGC5850.20230423.1009.fits [8.658 sec]
Remove 902 cosmic-ray for /data4/gecko/factory/loao/2023_0422/afzobj.NGC5850.20230423.1013.fits [8.77 sec]
Remove 805 cosmic-ray for /data4/gecko/factory/loao/2023_0422/afzobj.NGC5962.20230423.1017.fits [8.801 sec]
Remove 740 cosmic-ray for /data4/gecko/factory/loao/2023_0422/afzobj.NGC5962.20230423.1019.fits [8.808 sec]
Remove 845 cosmic-ray for /data4/gecko/factory/loao/2023_0422/afzobj.NGC5962.20230423.1015.fits [8.828 sec]
Remove 1041 cosmic-ray for /data4/gecko/factory/loao/2023_0422/afzobj.NGC6070.20230423.1021.fits [8.841 sec]
Remove 765 cosmic-ray for /data4/gecko/factory/loao/2023_0422/afzobj.NGC5850.20230423.1011.fits [8.913 sec]
Remove 1025 cosmic-ray for /data4/gecko/factory/loao/2023_0422/afzobj.NGC6070.20230423.1023.fits [8.979 sec]
Remove 799 cosmic-ray for /data4/gecko/factory/loao/2023_0422/afzobj.NGC5850.20230423.1010.fits [8.214 sec]
Remove 790 cosmic-ray for /

### Rename to IMSNG/GECKO Convention

In [17]:
fov = obsinfo['fov']*u.arcmin 
crafzimlist = []
for ims in ('{}/cra*.fits'.format(path_data), '{}/cra*.fit'.format(path_data), '{}/cra*.fts'.format(path_data)):
	crafzimlist.extend(sorted(glob.glob(ims)))
# for inim in sorted(glob.glob('{}/crafz*.fits'.format(path_data))): 
for inim in crafzimlist:
	obj = fits.getheader(inim)['object'] 
	#	Modify incorrect object header
	if (inim.replace('crafz', 'afz') in astrometryfailist) & (obj in alltbl['obj']): 
		robj, sep = tool_tbd.imsng_name_correction(inim, alltbl, radius=fov) 
	else:
		pass
	calib.fnamechange(inim, obs)

caliblist = sorted(glob.glob(path_data+'/Calib*.fits'))
ic_cal = ImageFileCollection(path_data, glob_include='Calib*0.fits', keywords='*')
os.system('chmod 777 {}'.format(path_data))
os.system('chmod 777 {}/*'.format(path_data))
#	Calib-*.fits TO SAVE PATH
f = open(path_data+'/object.txt', 'a')
f.write('obs obj dateobs filter exptime\n')
for inim in caliblist:
	img = os.path.basename(inim)
	part = img.split('-')
	line = '{} {} {} {} {}\n'.format(part[1], part[2], part[3]+'T'+part[4], part[5], part[6])
	print(line)
	f.write(line)
f.close()

#	DATA FOLDER TO SAVE PATH
# os.system('rm {}/afz*.fits {}/fz*.fits'.format(path_data, path_data))
os.system(f'rm {path_data}/*fz*.f*')
os.system(f'rm -rf {path_save}/{os.path.basename(path_data)}')
plt.close('all')

mv /data4/gecko/factory/loao/2023_0422/crafzobj.NGC5850.20230423.1009.fits /data4/gecko/factory/loao/2023_0422/Calib-LOAO-NGC5850-20230423-110055-B-60.fits
mv /data4/gecko/factory/loao/2023_0422/crafzobj.NGC5850.20230423.1010.fits /data4/gecko/factory/loao/2023_0422/Calib-LOAO-NGC5850-20230423-110212-B-60.fits
mv /data4/gecko/factory/loao/2023_0422/crafzobj.NGC5850.20230423.1011.fits /data4/gecko/factory/loao/2023_0422/Calib-LOAO-NGC5850-20230423-110329-B-60.fits
mv /data4/gecko/factory/loao/2023_0422/crafzobj.NGC5850.20230423.1012.fits /data4/gecko/factory/loao/2023_0422/Calib-LOAO-NGC5850-20230423-110449-R-60.fits
mv /data4/gecko/factory/loao/2023_0422/crafzobj.NGC5850.20230423.1013.fits /data4/gecko/factory/loao/2023_0422/Calib-LOAO-NGC5850-20230423-110606-R-60.fits
mv /data4/gecko/factory/loao/2023_0422/crafzobj.NGC5850.20230423.1014.fits /data4/gecko/factory/loao/2023_0422/Calib-LOAO-NGC5850-20230423-110723-R-60.fits
mv /data4/gecko/factory/loao/2023_0422/crafzobj.NGC5962.20230423

In [18]:
for calibim in caliblist:

	center, vertices = tool.get_wcs_coordinates(calibim)

	fits.setval(calibim, "RACENT", value=round(center[0].item(), 3), comment="RA CENTER [deg]")	
	fits.setval(calibim, "DECCENT", value=round(center[1].item(), 3), comment="DEC CENTER [deg]")	
	
	for ii, (_ra, _dec) in enumerate(vertices):
		# print(ii, _ra, _dec)
		fits.setval(calibim, f"RAPOLY{ii}", value=round(_ra, 3), comment=f"RA POLYGON {ii} [deg]")	
		fits.setval(calibim, f"DEPOLY{ii}", value=round(_dec, 3), comment=f"DEC POLYGON {ii} [deg]")
		

### Defringe
- Only for LOAO z, I, Y-bands

In [19]:
st_ = time.time()
if (obs == 'LOAO') & ('I' in ic_cal.filter(imagetyp='object').summary['filter']):
	dfim = '/home/paek/qsopy/fringe/LOAO/fringe_i_ori.fits'
	dfdat = '/home/paek/qsopy/fringe/LOAO/fringe_i.dat'
	dfimlist = []
	for inim in ic_cal.filter(imagetyp='object', filter='I').summary['file']:
		# dfimlist.append(calib.defringe(str(inim), dfim, dfdat))
		dfedim = calib.defringe(str(inim), dfim, dfdat)
		mvcom = 'mv {} {}'.format(dfedim, inim)
		print(mvcom)
		os.system(mvcom)
	# tdict['defringe'] = time.time() - st - tdict[list(tdict.keys())[-1]]
else:
	print('No images to defringe')
	pass
protbl['status'][protbl['process']=='defringe'] = True
protbl['time'][protbl['process']=='defringe'] = int(time.time() - st_)
#------------------------------------------------------------
print('='*60)
print('Calibration IS DONE.\t('+str(int(time.time() - starttime))+' sec)')
print('='*60)

No images to defringe
Calibration IS DONE.	(296 sec)


## Photometry

In [20]:
st_ = time.time()
print('#\tPhotometry')
path_infile = f'{path_data}/{os.path.basename(path_default_gphot)}'
path_new_gphot = f'{os.path.dirname(path_infile)}/gphot.config'

#	Copy default photometry configuration
cpcom = f'cp {path_default_gphot} {path_new_gphot}'
print(cpcom)
os.system(cpcom)

#	Read default photometry configuration
f = open(path_default_gphot, 'r')
lines = f.read().splitlines()
f.close()

#	Write photometry configuration
g = open(path_new_gphot, 'w')
for line in lines:
	if 'imkey' in line:
		line = f'imkey\t{path_data}/C*0.fits'
	else:
		pass
	g.write(line+'\n')
g.close()

if obs == 'DOAO':
	path_phot = path_phot_sg
else:
	path_phot = path_phot_mp

#	Execute
com = f'python {path_phot} {path_data} {ncores}'
# com = f'python {path_phot} {path_data} 1'
print(com)
os.system(com)

protbl['status'][protbl['process']=='photometry'] = True
protbl['time'][protbl['process']=='photometry'] = int(time.time() - st_)

#	Photometry
cp /home/paek/config/gphot.loao.config /data4/gecko/factory/loao/2023_0422/gphot.config
python ./phot/gregoryphot_mp_2021.py /data4/gecko/factory/loao/2023_0422 8
/data4/gecko/factory/loao/2023_0422/gphot.config
No transient catalog for photometry
#	42 images to do photometry
0	/data4/gecko/factory/loao/2023_0422/Calib-LOAO-NGC5850-20230423-110055-B-60.fits
1	/data4/gecko/factory/loao/2023_0422/Calib-LOAO-NGC5850-20230423-110212-B-60.fits
2	/data4/gecko/factory/loao/2023_0422/Calib-LOAO-NGC5850-20230423-110329-B-60.fits
3	/data4/gecko/factory/loao/2023_0422/Calib-LOAO-NGC5850-20230423-110449-R-60.fits
4	/data4/gecko/factory/loao/2023_0422/Calib-LOAO-NGC5850-20230423-110606-R-60.fits
5	/data4/gecko/factory/loao/2023_0422/Calib-LOAO-NGC5850-20230423-110723-R-60.fits
6	/data4/gecko/factory/loao/2023_0422/Calib-LOAO-NGC5962-20230423-110947-B-60.fits
7	/data4/gecko/factory/loao/2023_0422/Calib-LOAO-NGC5962-20230423-111104-B-60.fits
8	/data4/gecko/factory/loao/2023_0422/Calib-LO

> 
----- SExtractor 2.19.5 started on 2023-04-26 at 10:45:56 with 1 thread

> Setting catalog parameters

> WARNING: Not enough apertures provided in config.:
         some APER photometric values will remain blank 

> Reading detection filter
> Initializing Neural Network
> Reading Neural Network Weights

> WARNING: Not enough apertures provided in config.:
         some APER photometric values will remain blank 

> Initializing catalog
> Looking for Calib-LOAO-NGC5962-20230423-111221-B-60.fits
----- Measuring from: Calib-LOAO-NGC5962-20230423-111221-B-60.fits
      "NGC5962" / no ext. header / 2048x2048 / 32 bits (floats)
Detection+Measurement image: > Setting up background maps
> Setting up background map at line:   64
> 
----- SExtractor 2.19.5 started on 2023-04-26 at 10:45:56 with 1 thread

> Setting catalog parameters
> 
----- SExtractor 2.19.5 started on 2023-04-26 at 10:45:56 with 1 thread

> Setting catalog parameters
> 
----- SExtractor 2.19.5 started on 2023-04-26 at 10:45:

2. SOURCE EXTRACTOR
2. SOURCE EXTRACTOR
2. SOURCE EXTRACTOR
3. MATCHING
3. MATCHING
4. ZERO POINT CALCULATION for MAG_AUTO [1/7]
--------------------------------------------------
ALL					: 37
--------------------------------------------------
FLAG(<=2)				: 37
B REF. MAGCUT (12.0-20.0)		: 37
Berr REF. MAGERR CUT < 0.05		: 37
MAGERR_AUTO CUT < 0.05		: 13
TOTAL #					: 13
4. ZERO POINT CALCULATION for MAG_AUTO [1/7]
--------------------------------------------------
ALL					: 34
--------------------------------------------------
FLAG(<=2)				: 34
B REF. MAGCUT (12.0-20.0)		: 34
Berr REF. MAGERR CUT < 0.05		: 34
MAGERR_AUTO CUT < 0.05		: 12
TOTAL #					: 12
3. MATCHING
4. ZERO POINT CALCULATION for MAG_AUTO [1/7]
--------------------------------------------------
ALL					: 63
--------------------------------------------------
FLAG(<=2)				: 63
R REF. MAGCUT (12.0-20.0)		: 63
Rerr REF. MAGERR CUT < 0.05		: 63
MAGERR_AUTO CUT < 0.05		: 28
TOTAL #					: 28
MAG TYP     : MAG_AUTO
ZP         

4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER_1 [3/7]
--------------------------------------------------
ALL					: 37
--------------------------------------------------
FLAG(<=2)				: 37
B REF. MAGCUT (12.0-20.0)		: 37
Berr REF. MAGERR CUT < 0.05		: 37
MAGERR_APER_1 CUT < 0.05		: 19
TOTAL #					: 19
3. MATCHING
4. ZERO POINT CALCULATION for MAG_AUTO [1/7]
--------------------------------------------------
ALL					: 112
--------------------------------------------------
FLAG(<=2)				: 112
B REF. MAGCUT (12.0-20.0)		: 112
Berr REF. MAGERR CUT < 0.05		: 112
MAGERR_AUTO CUT < 0.05		: 60
TOTAL #					: 60
MAG TYP     : MAG_APER
ZP          = 23.6
ZP ERR      = 0.056
STD.NUMB    = 15
REJ.NUMB    = 1
CLIP UPPER  = 1
CTIP LOWER  = 0
4-1. PLOT
4. ZERO POINT CALCULATION for MAG_AUTO [1/7]
--------------------------------------------------
ALL					: 115
--------------------------------------------------
FLAG(<=2)				: 115
B REF. MAGCUT (12.0-20.0)		: 115
Berr REF. MAGERR CUT < 0.05	

FAIL TO DRAW ZEROPOINT GRAPH
4-2. CHANGE HEADER
2. SOURCE EXTRACTOR
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER_1 [3/7]
--------------------------------------------------
ALL					: 34
--------------------------------------------------
FLAG(<=2)				: 34
B REF. MAGCUT (12.0-20.0)		: 34
Berr REF. MAGERR CUT < 0.05		: 34
MAGERR_APER_1 CUT < 0.05		: 16
TOTAL #					: 16
MAG TYP     : MAG_APER_1
ZP          = 23.692
ZP ERR      = 0.053
STD.NUMB    = 19
REJ.NUMB    = 0
CLIP UPPER  = 0
CTIP LOWER  = 0
4-2. CHANGE HEADER
MAG TYP     : MAG_APER
ZP          = 24.154
ZP ERR      = 0.049
STD.NUMB    = 37
REJ.NUMB    = 2
CLIP UPPER  = 0
CTIP LOWER  = 2
4-1. PLOT
2. SOURCE EXTRACTOR
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER_2 [4/7]
--------------------------------------------------
ALL					: 37
--------------------------------------------------
FLAG(<=2)				: 37
B REF. MAGCUT (12.0-20.0)		: 37
Berr REF. MAGERR CUT < 0.05		: 37
MAGERR_APER_2 CUT < 0.05		: 16
TOTAL #	

...

/home/gecko/gppy/util/tool.py:949: RuntimeWarning: invalid value encountered in sqrt
  return np.sqrt(a**2.+b**2.)


MAG TYP     : MAG_APER
ZP          = 25.778
ZP ERR      = 0.04
STD.NUMB    = 679
REJ.NUMB    = 113
CLIP UPPER  = 51
CTIP LOWER  = 62
4-1. PLOT
FAIL TO DRAW ZEROPOINT GRAPH
4-2. CHANGE HEADER
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER_1 [3/7]
--------------------------------------------------
ALL					: 1311
--------------------------------------------------
FLAG(<=2)				: 1254
R REF. MAGCUT (12.0-20.0)		: 1311
Rerr REF. MAGERR CUT < 0.05		: 1311
MAGERR_APER_1 CUT < 0.05		: 845
TOTAL #					: 797


MAG TYP     : MAG_APER
ZP          = 25.653
ZP ERR      = 0.042
STD.NUMB    = 587
REJ.NUMB    = 102
CLIP UPPER  = 40
CTIP LOWER  = 62
4-1. PLOT
FAIL TO DRAW ZEROPOINT GRAPH
4-2. CHANGE HEADER
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER_1 [3/7]
--------------------------------------------------
ALL					: 1197
--------------------------------------------------
FLAG(<=2)				: 1143
R REF. MAGCUT (12.0-20.0)		: 1197
Rerr REF. MAGERR CUT < 0.05		: 1197
MAGERR_APER_1 CUT < 0.05		: 738
TOTAL #					: 691


MAG TYP     : MAG_APER_1
ZP          = 25.598
ZP ERR      = 0.043
STD.NUMB    = 690
REJ.NUMB    = 107
CLIP UPPER  = 52
CTIP LOWER  = 55
4-2. CHANGE HEADER
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER_2 [4/7]
--------------------------------------------------
ALL					: 1311
--------------------------------------------------
FLAG(<=2)				: 1254
R REF. MAGCUT (12.0-20.0)		: 1311
Rerr REF. MAGERR CUT < 0.05		: 1311
MAGERR_APER_2 CUT < 0.05		: 808
TOTAL #					: 759
MAG TYP     : MAG_APER_1
ZP          = 25.612
ZP ERR      = 0.044
STD.NUMB    = 601
REJ.NUMB    = 90
CLIP UPPER  = 33
CTIP LOWER  = 57
4-2. CHANGE HEADER
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER_2 [4/7]
--------------------------------------------------
ALL					: 1197
--------------------------------------------------
FLAG(<=2)				: 1143
R REF. MAGCUT (12.0-20.0)		: 1197
Rerr REF. MAGERR CUT < 0.05		: 1197
MAGERR_APER_2 CUT < 0.05		: 674
TOTAL #					: 630
MAG TYP     : MAG_APER_2
ZP          = 

MAG TYP     : MAG_APER_1
ZP          = 25.599
ZP ERR      = 0.051
STD.NUMB    = 473
REJ.NUMB    = 39
CLIP UPPER  = 15
CTIP LOWER  = 24
4-2. CHANGE HEADER
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER_2 [4/7]
--------------------------------------------------
ALL					: 808
--------------------------------------------------
FLAG(<=2)				: 777
R REF. MAGCUT (12.0-20.0)		: 808
Rerr REF. MAGERR CUT < 0.05		: 808
MAGERR_APER_2 CUT < 0.05		: 510
TOTAL #					: 487
MAG TYP     : MAG_APER_2
ZP          = 25.938
ZP ERR      = 0.043
STD.NUMB    = 435
REJ.NUMB    = 52
CLIP UPPER  = 25
CTIP LOWER  = 27
4-2. CHANGE HEADER
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER_3 [5/7]
--------------------------------------------------
ALL					: 808
--------------------------------------------------
FLAG(<=2)				: 777
R REF. MAGCUT (12.0-20.0)		: 808
Rerr REF. MAGERR CUT < 0.05		: 808
MAGERR_APER_3 CUT < 0.05		: 438
TOTAL #					: 419
MAG TYP     : MAG_APER_3
ZP          = 26.1
ZP E

## Image registering & combine

In [21]:
st_ = time.time()
print('IMAGE REGISTERING & COMBINE')
combined_images = []
step = (1/24/60)*60	# 1 hour
ic_cal_phot = ImageFileCollection(path_data, glob_include='Calib*0.fits', keywords='*')
calist = sorted(glob.glob('{}/Calib*.fits'.format(path_data)))
objlist = sorted(list(set(ic_cal_phot.summary['object'])))
filterlist = sorted(list(set(ic_cal_phot.summary['filter'])))
# obj = 'NGC3147'
# filte = 'R'
for obj in objlist:
	for filte in filterlist:
		imlist_tmp = sorted(glob.glob('{}/Calib*-{}-*-{}-*.fits'.format(path_data, obj, filte)))
		if len(imlist_tmp) == 0:
			pass
		elif len(imlist_tmp) == 1:
			inim = imlist_tmp[0]
			comim = inim.replace('.fits', '.com.fits')
			cpcom = f'cp {inim} {comim}'
			print(cpcom)
			os.system(cpcom)
		else:
			print(obj, filte)
			# ic_part = sorted(glob.glob('{}/Calib*{}*{}*.fits'.format(path_data, obj, filte)))

			jds = np.array([fits.getheader(inim)['jd'] for inim in imlist_tmp])
			delts = jds - np.min(jds)

			grouplist = []
			grouplists = []

			i = 0
			for i in range(len(delts)):
				#	Initial setting
				if i == 0:
					t0 = delts[i]
				#	Add last group to grouplists
				elif i == len(delts)-1:
					grouplists.append(grouplist)
				t1 = delts[i]
				# print(t0, t1)
				dif = np.abs(t0-t1)

				if dif < step:
					grouplist.append(imlist_tmp[i])
				#	Generate new group
				else:
					grouplists.append(grouplist)
					grouplist = [imlist_tmp[i]]	 
				t0 = t1
				
			for group in grouplists:
				print('-'*60)
				if len(group) > 1:
					ref_image = group[0]
					images_to_align = group[1:]
					for inim in group:
						print(inim)
					# _data, _hdr = fits.getdata(ref_image, header=True)
					# ximage, yimage = _data.shape
					# racent, decent = _hdr['RACENT'], _hdr['DECCENT']
					try:
						# outim = tool.swarpcomb(
						# 	images_to_align,
						# 	gain=obsinfo['gain'].value,
						# 	pixscale=obsinfo['pixscale'],
						# 	racent=racent,
						# 	decent=decent,
						# 	ximage=ximage,
						# 	yimage=yimage,
						# 	listname='obj.list',
						# 	path_save='.',
						# 	keys_to_get=[
						# 		'OBJECT',
						# 		'FILTER',
						# 		'RACENT',
						# 		'DECCENT',
						# 		'RAPOLY0',
						# 		'DEPOLY0',
						# 		'RAPOLY1',
						# 		'DEPOLY1',
						# 		'RAPOLY2',
						# 		'DEPOLY2',
						# 		'RAPOLY3',
						# 		'DEPOLY3',
						# 		]
						# 	)
						outim = tool.imcombine_routine(images_to_align, ref_image)
						combined_images.append(outim)
					except:
						print('Fail to image align & combine routine.')
						print(images_to_align)
						pass
				else:
					print('There is only one image.')
					combined_images.append(group[0])

protbl['status'][protbl['process']=='image_stack'] = True
protbl['time'][protbl['process']=='image_stack'] = int(time.time() - st_)

IMAGE REGISTERING & COMBINE
NGC5850 B
------------------------------------------------------------
/data4/gecko/factory/loao/2023_0422/Calib-LOAO-NGC5850-20230423-110055-B-60.fits
/data4/gecko/factory/loao/2023_0422/Calib-LOAO-NGC5850-20230423-110212-B-60.fits
/data4/gecko/factory/loao/2023_0422/Calib-LOAO-NGC5850-20230423-110329-B-60.fits


Reference image	: /data4/gecko/factory/loao/2023_0422/Calib-LOAO-NGC5850-20230423-110055-B-60.fits
Input images	:
/data4/gecko/factory/loao/2023_0422/Calib-LOAO-NGC5850-20230423-110212-B-60.fits
/data4/gecko/factory/loao/2023_0422/Calib-LOAO-NGC5850-20230423-110329-B-60.fits
#	IMAGE REGISTERING
##########  Preparing reference ...
No filter file found, using default filter
No NNW file found, using default NNW config


> 
----- SExtractor 2.19.5 started on 2023-04-26 at 10:47:33 with 1 thread

> Setting catalog parameters
> Reading detection filter
> Initializing catalog
> Looking for Calib-LOAO-NGC5850-20230423-110055-B-60.fits
----- Measuring from: Calib-LOAO-NGC5850-20230423-110055-B-60.fits
      "NGC5850" / no ext. header / 2048x2048 / 32 bits (floats)
Detection+Measurement image: > Setting up background maps
> Setting up background map at line:   64
> Setting up background map at line:  128
> Setting up background map at line:  192
> Setting up background map at line:  256
> Setting up background map at line:  320
> Setting up background map at line:  384
> Setting up background map at line:  448
> Setting up background map at line:  512
> Setting up background map at line:  576
> Setting up background map at line:  640
> Setting up background map at line:  704
> Setting up background map at line:  768
> Setting up background map at line:  832
> Setting up background map at line:  896
> Setting

Number of sources in catalog : 280
EXT_NUMBER values found in catalog : 1
I've selected 263 sources
Making more quads, from quadlevel 0 ...
Made   35 quads from  263 stars (combi n=7 s=0 d=30.0)
Removing 0/35 duplicates
########## Processing /data4/gecko/factory/loao/2023_0422/Calib-LOAO-NGC5850-20230423-110212-B-60.fits
No filter file found, using default filter
No NNW file found, using default NNW config


> 
----- SExtractor 2.19.5 started on 2023-04-26 at 10:47:33 with 1 thread

> Setting catalog parameters
> Reading detection filter
> Initializing catalog
> Looking for Calib-LOAO-NGC5850-20230423-110212-B-60.fits
----- Measuring from: Calib-LOAO-NGC5850-20230423-110212-B-60.fits
      "NGC5850" / no ext. header / 2048x2048 / 32 bits (floats)
Detection+Measurement image: > Setting up background maps
> Setting up background map at line:   64
> Setting up background map at line:  128
> Setting up background map at line:  192
> Setting up background map at line:  256
> Setting up background map at line:  320
> Setting up background map at line:  384
> Setting up background map at line:  448
> Setting up background map at line:  512
> Setting up background map at line:  576
> Setting up background map at line:  640
> Setting up background map at line:  704
> Setting up background map at line:  768
> Setting up background map at line:  832
> Setting up background map at line:  896
> Setting

...

Number of sources in catalog : 2008
EXT_NUMBER values found in catalog : 1
I've selected 1963 sources
Making more quads, from quadlevel 0 ...
Made   35 quads from  500 stars (combi n=7 s=0 d=30.0)
Removing 0/35 duplicates
########## Processing /data4/gecko/factory/loao/2023_0422/Calib-LOAO-NGC6946-20230423-115311-R-60.fits
No filter file found, using default filter
No NNW file found, using default NNW config


> 
----- SExtractor 2.19.5 started on 2023-04-26 at 10:48:26 with 1 thread

> Setting catalog parameters
> Reading detection filter
> Initializing catalog
> Looking for Calib-LOAO-NGC6946-20230423-115311-R-60.fits
----- Measuring from: Calib-LOAO-NGC6946-20230423-115311-R-60.fits
      "NGC6946" / no ext. header / 2048x2048 / 32 bits (floats)
Detection+Measurement image: > Setting up background maps
> Setting up background map at line:   64
> Setting up background map at line:  128
> Setting up background map at line:  192
> Setting up background map at line:  256
> Setting up background map at line:  320
> Setting up background map at line:  384
> Setting up background map at line:  448
> Setting up background map at line:  512
> Setting up background map at line:  576
> Setting up background map at line:  640
> Setting up background map at line:  704
> Setting up background map at line:  768
> Setting up background map at line:  832
> Setting up background map at line:  896
> Setting

Number of sources in catalog : 1924
EXT_NUMBER values found in catalog : 1
I've selected 1875 sources
Making more quads, from quadlevel 0 ...
Made   35 quads from  500 stars (combi n=7 s=0 d=30.0)
Removing 0/35 duplicates
Finding 4 best candidates among 35 x 35 (ukn x ref)
We have a maximum of 35 quad pairs
Cand  1 (dist.   0.00038718) : Rotation   -0.003023 [deg], scale 1.000296
Cand  2 (dist.   0.00055911) : Rotation   +0.046784 [deg], scale 1.000217
Cand  3 (dist.   0.00060415) : Rotation   +0.030724 [deg], scale 0.999750
Cand  4 (dist.   0.00074629) : Rotation   +0.046784 [deg], scale 1.000217
484/500 stars with distance < r = 5.0 (mean 0.3, median 0.3, std 0.2)
Filtered for companions, keeping 484/484 matches
Refitting transform (before/after) :
Rotation   -0.003023 [deg], scale 1.000296
Rotation   +0.000895 [deg], scale 0.999994
484/500 stars with distance < r = 5.0 (mean 0.1, median 0.0, std 0.2)
Filtered for companions, keeping 484/484 matches
I'm done !
Computed flux ratio fro

> 
----- SExtractor 2.19.5 started on 2023-04-26 at 10:48:27 with 1 thread

> Setting catalog parameters
> Reading detection filter
> Initializing catalog
> Looking for Calib-LOAO-NGC6946-20230423-115428-R-60.fits
----- Measuring from: Calib-LOAO-NGC6946-20230423-115428-R-60.fits
      "NGC6946" / no ext. header / 2048x2048 / 32 bits (floats)
Detection+Measurement image: > Setting up background maps
> Setting up background map at line:   64
> Setting up background map at line:  128
> Setting up background map at line:  192
> Setting up background map at line:  256
> Setting up background map at line:  320
> Setting up background map at line:  384
> Setting up background map at line:  448
> Setting up background map at line:  512
> Setting up background map at line:  576
> Setting up background map at line:  640
> Setting up background map at line:  704
> Setting up background map at line:  768
> Setting up background map at line:  832
> Setting up background map at line:  896
> Setting

Number of sources in catalog : 1803
EXT_NUMBER values found in catalog : 1
I've selected 1755 sources
Making more quads, from quadlevel 0 ...
Made   35 quads from  500 stars (combi n=7 s=0 d=30.0)
Removing 0/35 duplicates
Finding 4 best candidates among 35 x 35 (ukn x ref)
We have a maximum of 35 quad pairs
Cand  1 (dist.   0.00006848) : Rotation   -0.003391 [deg], scale 0.999943
Cand  2 (dist.   0.00045439) : Rotation   -0.003391 [deg], scale 0.999943
Cand  3 (dist.   0.00045680) : Rotation   -0.003391 [deg], scale 0.999943
Cand  4 (dist.   0.00047222) : Rotation   -0.010690 [deg], scale 1.000309
485/500 stars with distance < r = 5.0 (mean 0.2, median 0.1, std 0.2)
Filtered for companions, keeping 485/485 matches
Refitting transform (before/after) :
Rotation   -0.003391 [deg], scale 0.999943
Rotation   +0.002010 [deg], scale 0.999978
485/500 stars with distance < r = 5.0 (mean 0.1, median 0.0, std 0.2)
Filtered for companions, keeping 485/485 matches
I'm done !
Computed flux ratio fro

In [22]:
images_to_align = group
ref_image = images_to_align[0]

outim = tool.imcombine_routine(images_to_align, ref_image)

Reference image	: /data4/gecko/factory/loao/2023_0422/Calib-LOAO-NGC6946-20230423-115153-R-60.fits
Input images	:
/data4/gecko/factory/loao/2023_0422/Calib-LOAO-NGC6946-20230423-115153-R-60.fits
/data4/gecko/factory/loao/2023_0422/Calib-LOAO-NGC6946-20230423-115311-R-60.fits
/data4/gecko/factory/loao/2023_0422/Calib-LOAO-NGC6946-20230423-115428-R-60.fits
#	IMAGE REGISTERING
##########  Preparing reference ...
No filter file found, using default filter
No NNW file found, using default NNW config


> 
----- SExtractor 2.19.5 started on 2023-04-26 at 10:48:30 with 1 thread

> Setting catalog parameters
> Reading detection filter
> Initializing catalog
> Looking for Calib-LOAO-NGC6946-20230423-115153-R-60.fits
----- Measuring from: Calib-LOAO-NGC6946-20230423-115153-R-60.fits
      "NGC6946" / no ext. header / 2048x2048 / 32 bits (floats)
Detection+Measurement image: > Setting up background maps
> Setting up background map at line:   64
> Setting up background map at line:  128
> Setting up background map at line:  192
> Setting up background map at line:  256
> Setting up background map at line:  320
> Setting up background map at line:  384
> Setting up background map at line:  448
> Setting up background map at line:  512
> Setting up background map at line:  576
> Setting up background map at line:  640
> Setting up background map at line:  704
> Setting up background map at line:  768
> Setting up background map at line:  832
> Setting up background map at line:  896
> Setting

Number of sources in catalog : 2008
EXT_NUMBER values found in catalog : 1
I've selected 1963 sources
Making more quads, from quadlevel 0 ...
Made   35 quads from  500 stars (combi n=7 s=0 d=30.0)
Removing 0/35 duplicates
########## Processing /data4/gecko/factory/loao/2023_0422/Calib-LOAO-NGC6946-20230423-115153-R-60.fits
No filter file found, using default filter
No NNW file found, using default NNW config


> 
----- SExtractor 2.19.5 started on 2023-04-26 at 10:48:31 with 1 thread

> Setting catalog parameters
> Reading detection filter
> Initializing catalog
> Looking for Calib-LOAO-NGC6946-20230423-115153-R-60.fits
----- Measuring from: Calib-LOAO-NGC6946-20230423-115153-R-60.fits
      "NGC6946" / no ext. header / 2048x2048 / 32 bits (floats)
Detection+Measurement image: > Setting up background maps
> Setting up background map at line:   64
> Setting up background map at line:  128
> Setting up background map at line:  192
> Setting up background map at line:  256
> Setting up background map at line:  320
> Setting up background map at line:  384
> Setting up background map at line:  448
> Setting up background map at line:  512
> Setting up background map at line:  576
> Setting up background map at line:  640
> Setting up background map at line:  704
> Setting up background map at line:  768
> Setting up background map at line:  832
> Setting up background map at line:  896
> Setting

Number of sources in catalog : 2008
EXT_NUMBER values found in catalog : 1
I've selected 1963 sources
Making more quads, from quadlevel 0 ...
Made   35 quads from  500 stars (combi n=7 s=0 d=30.0)
Removing 0/35 duplicates
Finding 4 best candidates among 35 x 35 (ukn x ref)
We have a maximum of 35 quad pairs
Cand  1 (dist.   0.00000000) : Rotation   -0.000000 [deg], scale 1.000000
Cand  2 (dist.   0.00000000) : Rotation   -0.000000 [deg], scale 1.000000
Cand  3 (dist.   0.00000000) : Rotation   -0.000000 [deg], scale 1.000000
Cand  4 (dist.   0.00000000) : Rotation   -0.000000 [deg], scale 1.000000
500/500 stars with distance < r = 5.0 (mean 0.0, median 0.0, std 0.0)
Filtered for companions, keeping 500/500 matches
Refitting transform (before/after) :
Rotation   -0.000000 [deg], scale 1.000000
Rotation   +0.000000 [deg], scale 1.000000
500/500 stars with distance < r = 5.0 (mean 0.0, median 0.0, std 0.0)
Filtered for companions, keeping 500/500 matches
I'm done !
Computed flux ratio fro

> 
----- SExtractor 2.19.5 started on 2023-04-26 at 10:48:32 with 1 thread

> Setting catalog parameters
> Reading detection filter
> Initializing catalog
> Looking for Calib-LOAO-NGC6946-20230423-115311-R-60.fits
----- Measuring from: Calib-LOAO-NGC6946-20230423-115311-R-60.fits
      "NGC6946" / no ext. header / 2048x2048 / 32 bits (floats)
Detection+Measurement image: > Setting up background maps
> Setting up background map at line:   64
> Setting up background map at line:  128
> Setting up background map at line:  192
> Setting up background map at line:  256
> Setting up background map at line:  320
> Setting up background map at line:  384
> Setting up background map at line:  448
> Setting up background map at line:  512
> Setting up background map at line:  576
> Setting up background map at line:  640
> Setting up background map at line:  704
> Setting up background map at line:  768
> Setting up background map at line:  832
> Setting up background map at line:  896
> Setting

Number of sources in catalog : 1924
EXT_NUMBER values found in catalog : 1
I've selected 1875 sources
Making more quads, from quadlevel 0 ...
Made   35 quads from  500 stars (combi n=7 s=0 d=30.0)
Removing 0/35 duplicates
Finding 4 best candidates among 35 x 35 (ukn x ref)
We have a maximum of 35 quad pairs
Cand  1 (dist.   0.00038718) : Rotation   -0.003023 [deg], scale 1.000296
Cand  2 (dist.   0.00055911) : Rotation   +0.046784 [deg], scale 1.000217
Cand  3 (dist.   0.00060415) : Rotation   +0.030724 [deg], scale 0.999750
Cand  4 (dist.   0.00074629) : Rotation   +0.046784 [deg], scale 1.000217
484/500 stars with distance < r = 5.0 (mean 0.3, median 0.3, std 0.2)
Filtered for companions, keeping 484/484 matches
Refitting transform (before/after) :
Rotation   -0.003023 [deg], scale 1.000296
Rotation   +0.000895 [deg], scale 0.999994
484/500 stars with distance < r = 5.0 (mean 0.1, median 0.0, std 0.2)
Filtered for companions, keeping 484/484 matches
I'm done !
Computed flux ratio fro

> 
----- SExtractor 2.19.5 started on 2023-04-26 at 10:48:33 with 1 thread

> Setting catalog parameters
> Reading detection filter
> Initializing catalog
> Looking for Calib-LOAO-NGC6946-20230423-115428-R-60.fits
----- Measuring from: Calib-LOAO-NGC6946-20230423-115428-R-60.fits
      "NGC6946" / no ext. header / 2048x2048 / 32 bits (floats)
Detection+Measurement image: > Setting up background maps
> Setting up background map at line:   64
> Setting up background map at line:  128
> Setting up background map at line:  192
> Setting up background map at line:  256
> Setting up background map at line:  320
> Setting up background map at line:  384
> Setting up background map at line:  448
> Setting up background map at line:  512
> Setting up background map at line:  576
> Setting up background map at line:  640
> Setting up background map at line:  704
> Setting up background map at line:  768
> Setting up background map at line:  832
> Setting up background map at line:  896
> Setting

Number of sources in catalog : 1803
EXT_NUMBER values found in catalog : 1
I've selected 1755 sources
Making more quads, from quadlevel 0 ...
Made   35 quads from  500 stars (combi n=7 s=0 d=30.0)
Removing 0/35 duplicates
Finding 4 best candidates among 35 x 35 (ukn x ref)
We have a maximum of 35 quad pairs
Cand  1 (dist.   0.00006848) : Rotation   -0.003391 [deg], scale 0.999943
Cand  2 (dist.   0.00045439) : Rotation   -0.003391 [deg], scale 0.999943
Cand  3 (dist.   0.00045680) : Rotation   -0.003391 [deg], scale 0.999943
Cand  4 (dist.   0.00047222) : Rotation   -0.010690 [deg], scale 1.000309
485/500 stars with distance < r = 5.0 (mean 0.2, median 0.1, std 0.2)
Filtered for companions, keeping 485/485 matches
Refitting transform (before/after) :
Rotation   -0.003391 [deg], scale 0.999943
Rotation   +0.002010 [deg], scale 0.999978
485/500 stars with distance < r = 5.0 (mean 0.1, median 0.0, std 0.2)
Filtered for companions, keeping 485/485 matches
I'm done !
Computed flux ratio fro

## Photometry for combined images

In [23]:
st_ = time.time()
#	Write photometry configuration
h = open(path_new_gphot, 'w')
for line in lines:
	if 'imkey' in line:
		line = '{}\t{}/C*com.fits'.format('imkey', path_data)
	else:
		pass
	h.write(line+'\n')
h.close()
#	Execute
path_phot = path_phot_mp
com = 'python {} {} {}'.format(path_phot, path_data, ncores)
print(com)
os.system(com)
# tdict['photometry_com'] = time.time() - st - tdict[list(tdict.keys())[-1]]
protbl['status'][protbl['process']=='photometry_com'] = True
protbl['time'][protbl['process']=='photometry_com'] = int(time.time() - st_)

ic_com_phot = ImageFileCollection(path_data, glob_include='Calib*com.fits', keywords='*')	
#	Summary
print('Draw observation summary plots')
# for filte in list(set(ic_cal_phot.summary['filter'])):
for filte in filterlist:
	try:
		tool.obs_summary(filte, ic_cal_phot, ic_com_phot, path_save=path_data)
	except:
		print('Fail to make summary plots.')
		pass
	plt.close('all')

python ./phot/gregoryphot_mp_2021.py /data4/gecko/factory/loao/2023_0422 8
/data4/gecko/factory/loao/2023_0422/gphot.config
No transient catalog for photometry
#	15 images to do photometry
0	/data4/gecko/factory/loao/2023_0422/Calib-LOAO-NGC5850-20230423-110224-B-180.com.fits
1	/data4/gecko/factory/loao/2023_0422/Calib-LOAO-NGC5850-20230423-110614-R-180.com.fits
2	/data4/gecko/factory/loao/2023_0422/Calib-LOAO-NGC5962-20230423-111102-B-180.com.fits
3	/data4/gecko/factory/loao/2023_0422/Calib-LOAO-NGC5962-20230423-111521-R-180.com.fits
4	/data4/gecko/factory/loao/2023_0422/Calib-LOAO-NGC6070-20230423-111940-B-180.com.fits
5	/data4/gecko/factory/loao/2023_0422/Calib-LOAO-NGC6070-20230423-112400-R-180.com.fits
6	/data4/gecko/factory/loao/2023_0422/Calib-LOAO-NGC6090-20230423-104955-B-180.com.fits
7	/data4/gecko/factory/loao/2023_0422/Calib-LOAO-NGC6090-20230423-105345-R-180.com.fits
8	/data4/gecko/factory/loao/2023_0422/Calib-LOAO-NGC6555-20230423-112916-B-180.com.fits
9	/data4/gecko/fact

> 
----- SExtractor 2.19.5 started on 2023-04-26 at 10:48:39 with 1 thread

> Setting catalog parameters

> WARNING: Not enough apertures provided in config.:
         some APER photometric values will remain blank 

> Reading detection filter
> Initializing Neural Network
> Reading Neural Network Weights
> 
----- SExtractor 2.19.5 started on 2023-04-26 at 10:48:39 with 1 thread

> Setting catalog parameters

> WARNING: Not enough apertures provided in config.:
         some APER photometric values will remain blank 

> Initializing catalog

> WARNING: Not enough apertures provided in config.:
         some APER photometric values will remain blank 

> Reading detection filter
> Initializing Neural Network
> Reading Neural Network Weights
> Looking for Calib-LOAO-NGC5850-20230423-110224-B-180.com.fits

> WARNING: Not enough apertures provided in config.:
         some APER photometric values will remain blank 

> 
----- SExtractor 2.19.5 started on 2023-04-26 at 10:48:39 with 1 thread


2. SOURCE EXTRACTOR
2. SOURCE EXTRACTOR
3. MATCHING
2. SOURCE EXTRACTOR
2. SOURCE EXTRACTOR
4. ZERO POINT CALCULATION for MAG_AUTO [1/7]
--------------------------------------------------
ALL					: 57
--------------------------------------------------
FLAG(<=2)				: 57
B REF. MAGCUT (12.0-20.0)		: 57
Berr REF. MAGERR CUT < 0.05		: 57
MAGERR_AUTO CUT < 0.05		: 24
TOTAL #					: 23
3. MATCHING
4. ZERO POINT CALCULATION for MAG_AUTO [1/7]
--------------------------------------------------
ALL					: 71
--------------------------------------------------
FLAG(<=2)				: 71
B REF. MAGCUT (12.0-20.0)		: 71
Berr REF. MAGERR CUT < 0.05		: 71
MAGERR_AUTO CUT < 0.05		: 35
TOTAL #					: 35
3. MATCHING
3. MATCHING
MAG TYP     : MAG_AUTO
ZP          = 24.293
ZP ERR      = 0.07
STD.NUMB    = 22
REJ.NUMB    = 1
CLIP UPPER  = 1
CTIP LOWER  = 0
4-2. CHANGE HEADER
4. ZERO POINT CALCULATION for MAG_AUTO [1/7]
--------------------------------------------------
ALL					: 88
------------------------------------

4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER [2/7]
--------------------------------------------------
ALL					: 88
--------------------------------------------------
FLAG(<=2)				: 88
R REF. MAGCUT (12.0-20.0)		: 88
Rerr REF. MAGERR CUT < 0.05		: 88
MAGERR_APER CUT < 0.05		: 53
TOTAL #					: 53
3. MATCHING
FAIL TO DRAW ZEROPOINT GRAPH
4-2. CHANGE HEADER
MAG TYP     : MAG_AUTO
ZP          = 25.301
ZP ERR      = 0.034
STD.NUMB    = 50
REJ.NUMB    = 11
CLIP UPPER  = 5
CTIP LOWER  = 6
4-2. CHANGE HEADER
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER_1 [3/7]
--------------------------------------------------
ALL					: 57
--------------------------------------------------
FLAG(<=2)				: 57
B REF. MAGCUT (12.0-20.0)		: 57
Berr REF. MAGERR CUT < 0.05		: 57
MAGERR_APER_1 CUT < 0.05		: 32
TOTAL #					: 32
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER [2/7]
--------------------------------------------------
ALL					: 105
-------------------------------

FAIL TO DRAW ZEROPOINT GRAPH
4-2. CHANGE HEADER
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER_1 [3/7]
--------------------------------------------------
ALL					: 71
--------------------------------------------------
FLAG(<=2)				: 71
B REF. MAGCUT (12.0-20.0)		: 71
Berr REF. MAGERR CUT < 0.05		: 71
MAGERR_APER_1 CUT < 0.05		: 44
TOTAL #					: 44
2. SOURCE EXTRACTOR
MAG TYP     : MAG_APER_1
ZP          = 23.862
ZP ERR      = 0.064
STD.NUMB    = 28
REJ.NUMB    = 4
MAG TYP     : MAG_APER
ZP          = 24.232
ZP ERR      = 0.039
STD.NUMB    = 48
REJ.NUMB    = 5
CLIP UPPER  = 1
CLIP UPPER  = 1
CTIP LOWER  = 3
4-2. CHANGE HEADER
CTIP LOWER  = 4
4-1. PLOT
MAG TYP     : MAG_APER
ZP          = 24.956
ZP ERR      = 0.057
STD.NUMB    = 68
REJ.NUMB    = 4
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER_2 [4/7]
CLIP UPPER  = 3
--------------------------------------------------
ALL					: 57
--------------------------------------------------
FLAG(<=2)				: 57
B REF. MAGCU

...

MAG TYP     : MAG_APER_1
ZP          = 25.397
ZP ERR      = 0.045
STD.NUMB    = 503
REJ.NUMB    = 78
CLIP UPPER  = 46
CTIP LOWER  = 32
4-2. CHANGE HEADER
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER_2 [4/7]
--------------------------------------------------
ALL					: 1082
--------------------------------------------------
FLAG(<=2)				: 1037
B REF. MAGCUT (12.0-20.0)		: 1077
Berr REF. MAGERR CUT < 0.05		: 1078
MAGERR_APER_2 CUT < 0.05		: 612
TOTAL #					: 574
MAG TYP     : MAG_APER_2
ZP          = 25.731
ZP ERR      = 0.042
STD.NUMB    = 506
REJ.NUMB    = 68
CLIP UPPER  = 47
CTIP LOWER  = 21
4-2. CHANGE HEADER
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER_3 [5/7]
--------------------------------------------------
ALL					: 1082
--------------------------------------------------
FLAG(<=2)				: 1037
B REF. MAGCUT (12.0-20.0)		: 1077
Berr REF. MAGERR CUT < 0.05		: 1078
MAGERR_APER_3 CUT < 0.05		: 543
TOTAL #					: 507
3. MATCHING
4. ZERO POINT CALCULATION fo

2. SOURCE EXTRACTOR
MAG TYP     : MAG_APER_1
ZP          = 25.592
ZP ERR      = 0.046
STD.NUMB    = 593
REJ.NUMB    = 73
CLIP UPPER  = 33
CTIP LOWER  = 40
4-2. CHANGE HEADER
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER_2 [4/7]
--------------------------------------------------
ALL					: 1074
--------------------------------------------------
FLAG(<=2)				: 1022
R REF. MAGCUT (12.0-20.0)		: 1074
Rerr REF. MAGERR CUT < 0.05		: 1074
MAGERR_APER_2 CUT < 0.05		: 693
TOTAL #					: 648
MAG TYP     : MAG_APER_2
ZP          = 25.931
ZP ERR      = 0.04
STD.NUMB    = 559
REJ.NUMB    = 89
CLIP UPPER  = 45
CTIP LOWER  = 44
4-2. CHANGE HEADER
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER_3 [5/7]
--------------------------------------------------
ALL					: 1074
--------------------------------------------------
FLAG(<=2)				: 1022
R REF. MAGCUT (12.0-20.0)		: 1074
Rerr REF. MAGERR CUT < 0.05		: 1074
MAGERR_APER_3 CUT < 0.05		: 606
TOTAL #					: 563
MAG TYP     : MAG_APE

FAIL TO DRAW ZEROPOINT GRAPH
4-2. CHANGE HEADER
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER_1 [3/7]
--------------------------------------------------
ALL					: 1100
--------------------------------------------------
FLAG(<=2)				: 1042
R REF. MAGCUT (12.0-20.0)		: 1100
Rerr REF. MAGERR CUT < 0.05		: 1100
MAGERR_APER_1 CUT < 0.05		: 740
TOTAL #					: 690
MAG TYP     : MAG_APER_1
ZP          = 25.603
ZP ERR      = 0.046
STD.NUMB    = 609
REJ.NUMB    = 81
CLIP UPPER  = 39
CTIP LOWER  = 42
4-2. CHANGE HEADER
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER_2 [4/7]
--------------------------------------------------
ALL					: 1100
--------------------------------------------------
FLAG(<=2)				: 1042
R REF. MAGCUT (12.0-20.0)		: 1100
Rerr REF. MAGERR CUT < 0.05		: 1100
MAGERR_APER_2 CUT < 0.05		: 712
TOTAL #					: 662
MAG TYP     : MAG_APER_2
ZP          = 25.937
ZP ERR      = 0.042
STD.NUMB    = 583
REJ.NUMB    = 79
CLIP UPPER  = 44
CTIP LOWER  = 35
4-2. CHANGE

MAG TYP     : MAG_AUTO
ZP          = 26.135
ZP ERR      = 0.029
STD.NUMB    = 565
REJ.NUMB    = 265
CLIP UPPER  = 142
CTIP LOWER  = 123
4-2. CHANGE HEADER
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER [2/7]
--------------------------------------------------
ALL					: 1682
--------------------------------------------------
FLAG(<=2)				: 1545
R REF. MAGCUT (12.0-20.0)		: 1682
Rerr REF. MAGERR CUT < 0.05		: 1682
MAGERR_APER CUT < 0.05		: 1095
TOTAL #					: 984
MAG TYP     : MAG_APER_1
ZP          = 25.572
ZP ERR      = 0.041
STD.NUMB    = 777
REJ.NUMB    = 153
CLIP UPPER  = 68
CTIP LOWER  = 85
4-2. CHANGE HEADER
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER_2 [4/7]
--------------------------------------------------
ALL					: 1632
--------------------------------------------------
FLAG(<=2)				: 1520
R REF. MAGCUT (12.0-20.0)		: 1632
Rerr REF. MAGERR CUT < 0.05		: 1632
MAGERR_APER_2 CUT < 0.05		: 967
TOTAL #					: 873
MAG TYP     : MAG_APER
ZP          = 25.8

MAG TYP     : MAG_APER_2
ZP          = 25.866
ZP ERR      = 0.036
STD.NUMB    = 728
REJ.NUMB    = 145
CLIP UPPER  = 78
CTIP LOWER  = 67
4-2. CHANGE HEADER
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER_3 [5/7]
--------------------------------------------------
ALL					: 1632
--------------------------------------------------
FLAG(<=2)				: 1520
R REF. MAGCUT (12.0-20.0)		: 1632
Rerr REF. MAGERR CUT < 0.05		: 1632
MAGERR_APER_3 CUT < 0.05		: 795
TOTAL #					: 713
MAG TYP     : MAG_APER_1
ZP          = 25.589
ZP ERR      = 0.041
STD.NUMB    = 799
REJ.NUMB    = 190
CLIP UPPER  = 92
CTIP LOWER  = 98
4-2. CHANGE HEADER
4-3. PHOTOMETRY TABLE
4. ZERO POINT CALCULATION for MAG_APER_2 [4/7]
--------------------------------------------------
ALL					: 1682
--------------------------------------------------
FLAG(<=2)				: 1545
R REF. MAGCUT (12.0-20.0)		: 1682
Rerr REF. MAGERR CUT < 0.05		: 1682
MAGERR_APER_2 CUT < 0.05		: 1078
TOTAL #					: 970
MAG TYP     : MAG_APER_3
ZP          

#	Image subtraction


In [24]:
print('IMAGE SUBTRACTION')
subtracted_images = []
ds9comlist = []
for inim in combined_images:
	hdr = fits.getheader(inim)
	# obs = os.path.basename(inim).split('-')[1]
	# obs = 'LOAO'
	obj = hdr['object']
	filte = hdr['filter']
	path_refim = '/data3/paek/factory/ref_frames/{}'.format(obs)
	refimlist = glob.glob('{}/Ref*{}*{}*.fits'.format(path_refim, obj, filte))
	if len(refimlist) > 0:
		refim = refimlist[0]

		# subim, ds9com = tool.subtraction_routine3(inim, refim)

		# if False:
		if obs not in ['LSGT', 'DOAO', 'RASA36', 'SAO_C361K',]:
			subim, ds9com = tool.subtraction_routine(inim, refim)
		else:
			subim, ds9com = tool.subtraction_routine2(inim, refim)
			if os.path.getsize(subim) != 0:
				rmcom = f"rm {subim}"
				print(rmcom)
				os.system(rmcom)
				subim, ds9com = tool.subtraction_routine(inim, refim)
			else:
				pass

		subtracted_images.append(subim)
		ds9comlist.append(ds9com)
	else:
		print('There is no reference image for {}'.format(os.path.basename(inim)))
		pass
rmcom = 'rm {}/*Ref*gregister.fits'.format(path_data)
print(rmcom)
os.system(rmcom)
# tdict['subtraction'] = time.time() - st - tdict[list(tdict.keys())[-1]]
protbl['status'][protbl['process']=='subtraction'] = True
protbl['time'][protbl['process']=='subtraction'] = int(time.time() - st_)

IMAGE SUBTRACTION
##########  Preparing reference ...
No filter file found, using default filter
No NNW file found, using default NNW config


> 
----- SExtractor 2.19.5 started on 2023-04-26 at 10:49:30 with 1 thread

> Setting catalog parameters
> Reading detection filter
> Initializing catalog
> Looking for Calib-LOAO-NGC5850-20230423-110224-B-180.com.fits
----- Measuring from: Calib-LOAO-NGC5850-20230423-110224-B-180.com.fits
      "NGC5850" / no ext. header / 2048x2048 / 32 bits (floats)
Detection+Measurement image: > Setting up background maps
> Setting up background map at line:   64
> Setting up background map at line:  128
> Setting up background map at line:  192
> Setting up background map at line:  256
> Setting up background map at line:  320
> Setting up background map at line:  384
> Setting up background map at line:  448
> Setting up background map at line:  512
> Setting up background map at line:  576
> Setting up background map at line:  640
> Setting up background map at line:  704
> Setting up background map at line:  768
> Setting up background map at line:  832
> Setting up background map at line:  896

Number of sources in catalog : 372
EXT_NUMBER values found in catalog : 1
I've selected 352 sources
Making more quads, from quadlevel 0 ...
Made   35 quads from  352 stars (combi n=7 s=0 d=30.0)
Removing 0/35 duplicates
########## Processing /data3/paek/factory/ref_frames/LOAO/Ref-LOAO-NGC5850-0-0-B-0.fits
No filter file found, using default filter
No NNW file found, using default NNW config


> Setting up background map at line:   64
> Setting up background map at line:  128
> Setting up background map at line:  192
> Setting up background map at line:  256
> Setting up background map at line:  320
> Setting up background map at line:  384
> Setting up background map at line:  448
> Setting up background map at line:  512
> Setting up background map at line:  576
> Setting up background map at line:  640
> Setting up background map at line:  704
> Setting up background map at line:  768
> Setting up background map at line:  832
> Setting up background map at line:  896
> Setting up background map at line:  960
> Setting up background map at line: 1024
> Setting up background map at line: 1088
> Setting up background map at line: 1152
> Setting up background map at line: 1216
> Setting up background map at line: 1280
> Setting up background map at line: 1344
> Setting up background map at line: 1408
> Setting up background map at line: 1472
> Setting up background map at lin

Number of sources in catalog : 418
EXT_NUMBER values found in catalog : 1
I've selected 402 sources
Making more quads, from quadlevel 0 ...
Made   35 quads from  402 stars (combi n=7 s=0 d=30.0)
Removing 0/35 duplicates
Finding 4 best candidates among 35 x 35 (ukn x ref)
We have a maximum of 35 quad pairs
Cand  1 (dist.   0.00029724) : Rotation   +0.116722 [deg], scale 0.999836
Cand  2 (dist.   0.00034207) : Rotation   +0.116722 [deg], scale 0.999836
Cand  3 (dist.   0.00039435) : Rotation   +0.116722 [deg], scale 0.999836
Cand  4 (dist.   0.00047363) : Rotation   +0.122210 [deg], scale 0.999769
349/402 stars with distance < r = 5.0 (mean 0.3, median 0.2, std 0.3)
Filtered for companions, keeping 349/349 matches
Refitting transform (before/after) :
Rotation   +0.116722 [deg], scale 0.999836
Rotation   +0.118091 [deg], scale 0.999985
349/402 stars with distance < r = 5.0 (mean 0.2, median 0.2, std 0.2)
Filtered for companions, keeping 349/349 matches
I'm done !
Computed flux ratio from 

...

> 
----- SExtractor 2.19.5 started on 2023-04-26 at 10:52:18 with 1 thread

> Setting catalog parameters
> Reading detection filter
> Initializing catalog
> Looking for Ref-LOAO-NGC6946-0-0-R-0.fits
----- Measuring from: Ref-LOAO-NGC6946-0-0-R-0.fits
      "NGC6946" / no ext. header / 2048x2048 / 32 bits (floats)
Detection+Measurement image: > Setting up background maps
> Setting up background map at line:   64
> Setting up background map at line:  128
> Setting up background map at line:  192
> Setting up background map at line:  256
> Setting up background map at line:  320
> Setting up background map at line:  384
> Setting up background map at line:  448
> Setting up background map at line:  512
> Setting up background map at line:  576
> Setting up background map at line:  640
> Setting up background map at line:  704
> Setting up background map at line:  768
> Setting up background map at line:  832
> Setting up background map at line:  896
> Setting up background map at line:  9

Number of sources in catalog : 5087
EXT_NUMBER values found in catalog : 1
I've selected 5017 sources
Making more quads, from quadlevel 0 ...
Made   35 quads from  500 stars (combi n=7 s=0 d=30.0)
Removing 0/35 duplicates
Finding 4 best candidates among 35 x 35 (ukn x ref)
We have a maximum of 35 quad pairs
Cand  1 (dist.   0.00031155) : Rotation   +0.010551 [deg], scale 0.999957
Cand  2 (dist.   0.00048135) : Rotation   +0.036606 [deg], scale 1.000126
Cand  3 (dist.   0.00049452) : Rotation   +0.036606 [deg], scale 1.000126
Cand  4 (dist.   0.00057612) : Rotation   +0.010551 [deg], scale 0.999957
466/500 stars with distance < r = 5.0 (mean 0.5, median 0.5, std 0.4)
Filtered for companions, keeping 465/466 matches
Refitting transform (before/after) :
Rotation   +0.010551 [deg], scale 0.999957
Rotation   +0.008833 [deg], scale 0.999932
465/500 stars with distance < r = 5.0 (mean 0.2, median 0.2, std 0.4)
Filtered for companions, keeping 464/465 matches
I'm done !
Computed flux ratio fro

Doing : /data4/gecko/factory/loao/2023_0422/Calib-LOAO-NGC6946-20230423-115248-R-180.com.fits -
        /data4/gecko/factory/loao/2023_0422/Ref-LOAO-NGC6946-0-0-R-0_gregister.fits =
        /data4/gecko/factory/loao/2023_0422/hdCalib-LOAO-NGC6946-20230423-115248-R-180.com.fits
   Good templ data : -100000.0 -> 6000000000.0
   Good image data : -100000.0 -> 60000.0
Mallocing massive amounts of memory...
Region 0 pixels            : 1:2048,1:2048
 Vector Indices (buffered) : 0:2047,0:2047
 Vector Indices (good data): 0:2047,0:2047
Build stamp  : t    0 i    0 (grid coord  0  0)
Build stamp  : t    1 i    0 (grid coord  1  0)
Build stamp  : t    2 i    0 (grid coord  2  0)
Build stamp  : t    3 i    0 (grid coord  3  0)
Build stamp  : t    4 i    0 (grid coord  4  0)
Build stamp  : t    5 i    0 (grid coord  5  0)
Build stamp  : t    6 i    0 (grid coord  6  0)
Build stamp  : t    7 i    0 (grid coord  7  0)
Build stamp  : t    8 i    0 (grid coord  8  0)
Build stamp  : t    9 i    0 (gri

rm /data4/gecko/factory/loao/2023_0422/*Ref*gregister.fits


   Mean   : 0.00
   Median : 0.00
   Mode   : 0.00
   Stdev  : 10000000000.00
 Emperical / Expected Noise for OK pixels = inf

Region 0 finished

SUCCESS


##	Photometry for subtracted images


In [25]:
st_ = time.time()
#	Write photometry configuration
s = open(path_new_gphot, 'w')
for line in lines:
	if 'imkey' in line:
		# line = '{}\t{}/hd*com.fits'.format('imkey', path_data)
		line = '{}\t{}/hd*.fits'.format('imkey', path_data)
	else:
		pass
	if 'photfraction' in line:
		line = '{}\t{}'.format('photfraction', 1.0)
	else:
		pass
	if 'DETECT_MINAREA' in line:
		line = '{}\t{}'.format('DETECT_MINAREA', 10)
	else:
		pass
	if 'DETECT_THRESH' in line:
		line = '{}\t{}'.format('DETECT_THRESH', 1.25)
	else:
		pass
	s.write(line+'\n')
s.close()
#	Execute
hdimlist = sorted(glob.glob('{}/hd*.fits'.format(path_data)))
if len(hdimlist) > 0:
	com = 'python {} {}'.format(path_phot_sub, path_data)
	print(com)
	os.system(com)
	# tdict['photometry_sub'] = time.time() - st - tdict[list(tdict.keys())[-1]]
else:
	print('No subtracted image.')
	pass
protbl['status'][protbl['process']=='photometry_sub'] = True
protbl['time'][protbl['process']=='photometry_sub'] = int(time.time() - st_)

python ./phot/gregoryphot_sub_2021.py /data4/gecko/factory/loao/2023_0422
/data4/gecko/factory/loao/2023_0422/gphot.config
No transient catalog for photometry
#	14 images to do photometry
0	/data4/gecko/factory/loao/2023_0422/hdCalib-LOAO-NGC5850-20230423-110224-B-180.com.fits
1	/data4/gecko/factory/loao/2023_0422/hdCalib-LOAO-NGC5850-20230423-110614-R-180.com.fits
2	/data4/gecko/factory/loao/2023_0422/hdCalib-LOAO-NGC5962-20230423-111102-B-180.com.fits
3	/data4/gecko/factory/loao/2023_0422/hdCalib-LOAO-NGC5962-20230423-111521-R-180.com.fits
4	/data4/gecko/factory/loao/2023_0422/hdCalib-LOAO-NGC6070-20230423-111940-B-180.com.fits
5	/data4/gecko/factory/loao/2023_0422/hdCalib-LOAO-NGC6070-20230423-112400-R-180.com.fits
6	/data4/gecko/factory/loao/2023_0422/hdCalib-LOAO-NGC6090-20230423-104955-B-180.com.fits
7	/data4/gecko/factory/loao/2023_0422/hdCalib-LOAO-NGC6090-20230423-105345-R-180.com.fits
8	/data4/gecko/factory/loao/2023_0422/hdCalib-LOAO-NGC6555-20230423-112916-B-180.com.fits
9	

> 
----- SExtractor 2.19.5 started on 2023-04-26 at 10:52:33 with 1 thread

> Setting catalog parameters
> Reading detection filter
> Initializing Neural Network
> Reading Neural Network Weights
> Initializing check-image(s)
> Initializing catalog
> Looking for hdCalib-LOAO-NGC5850-20230423-110224-B-180.com.fits
----- Measuring from: hdCalib-LOAO-NGC5850-20230423-110224-B-180.com.fits
      "NGC5850" / no ext. header / 2048x2048 / 32 bits (floats)
Detection+Measurement image: > Setting up background maps
> Setting up background map at line:   64
> Setting up background map at line:  128
> Setting up background map at line:  192
> Setting up background map at line:  256
> Setting up background map at line:  320
> Setting up background map at line:  384
> Setting up background map at line:  448
> Setting up background map at line:  512
> Setting up background map at line:  576
> Setting up background map at line:  640
> Setting up background map at line:  704
> Setting up background map 

ZERO POINT CALCULATION for MAG_AUTO
ZERO POINT CALCULATION for MAG_APER
ZERO POINT CALCULATION for MAG_APER_1
ZERO POINT CALCULATION for MAG_APER_2
ZERO POINT CALCULATION for MAG_APER_3
ZERO POINT CALCULATION for MAG_APER_4
ZERO POINT CALCULATION for MAG_APER_5
------------------------------------------------------------
[2/14] /data4/gecko/factory/loao/2023_0422/hdCalib-LOAO-NGC5850-20230423-110614-R-180.com.fits
LOAO	NGC5850 in R-band
------------------------------------------------------------
2. SOURCE EXTRACTOR
sex -c /home/paek/config/gregoryphot.sex /data4/gecko/factory/loao/2023_0422/hdCalib-LOAO-NGC5850-20230423-110614-R-180.com.fits -CATALOG_NAME /data4/gecko/factory/loao/2023_0422/hdCalib-LOAO-NGC5850-20230423-110614-R-180.com.cat -CATALOG_TYPE ASCII_HEAD -PARAMETERS_NAME /home/paek/config/gregoryphot.param -DETECT_TYPE CCD -DETECT_MINAREA 10 -DETECT_MAXAREA 0 -DETECT_THRESH 1.25 -ANALYSIS_THRESH 1.5 -FILTER Y -FILTER_NAME /home/paek/config/gregoryphot.conv -DEBLEND_NTHRESH 

> 
----- SExtractor 2.19.5 started on 2023-04-26 at 10:52:34 with 1 thread

> Setting catalog parameters
> Reading detection filter
> Initializing Neural Network
> Reading Neural Network Weights
> Initializing check-image(s)
> Initializing catalog
> Looking for hdCalib-LOAO-NGC5850-20230423-110614-R-180.com.fits
----- Measuring from: hdCalib-LOAO-NGC5850-20230423-110614-R-180.com.fits
      "NGC5850" / no ext. header / 2048x2048 / 32 bits (floats)
Detection+Measurement image: > Setting up background maps
> Setting up background map at line:   64
> Setting up background map at line:  128
> Setting up background map at line:  192
> Setting up background map at line:  256
> Setting up background map at line:  320
> Setting up background map at line:  384
> Setting up background map at line:  448
> Setting up background map at line:  512
> Setting up background map at line:  576
> Setting up background map at line:  640
> Setting up background map at line:  704
> Setting up background map 

ZERO POINT CALCULATION for MAG_AUTO
ZERO POINT CALCULATION for MAG_APER
ZERO POINT CALCULATION for MAG_APER_1
ZERO POINT CALCULATION for MAG_APER_2
ZERO POINT CALCULATION for MAG_APER_3
ZERO POINT CALCULATION for MAG_APER_4
ZERO POINT CALCULATION for MAG_APER_5
------------------------------------------------------------
[3/14] /data4/gecko/factory/loao/2023_0422/hdCalib-LOAO-NGC5962-20230423-111102-B-180.com.fits
LOAO	NGC5962 in B-band
------------------------------------------------------------
2. SOURCE EXTRACTOR
sex -c /home/paek/config/gregoryphot.sex /data4/gecko/factory/loao/2023_0422/hdCalib-LOAO-NGC5962-20230423-111102-B-180.com.fits -CATALOG_NAME /data4/gecko/factory/loao/2023_0422/hdCalib-LOAO-NGC5962-20230423-111102-B-180.com.cat -CATALOG_TYPE ASCII_HEAD -PARAMETERS_NAME /home/paek/config/gregoryphot.param -DETECT_TYPE CCD -DETECT_MINAREA 10 -DETECT_MAXAREA 0 -DETECT_THRESH 1.25 -ANALYSIS_THRESH 1.5 -FILTER Y -FILTER_NAME /home/paek/config/gregoryphot.conv -DEBLEND_NTHRESH 

...

ZERO POINT CALCULATION for MAG_AUTO
ZERO POINT CALCULATION for MAG_APER
ZERO POINT CALCULATION for MAG_APER_1
ZERO POINT CALCULATION for MAG_APER_2
ZERO POINT CALCULATION for MAG_APER_3
ZERO POINT CALCULATION for MAG_APER_4
ZERO POINT CALCULATION for MAG_APER_5
------------------------------------------------------------
[13/14] /data4/gecko/factory/loao/2023_0422/hdCalib-LOAO-NGC6946-20230423-114926-B-180.com.fits
LOAO	NGC6946 in B-band
------------------------------------------------------------
2. SOURCE EXTRACTOR
sex -c /home/paek/config/gregoryphot.sex /data4/gecko/factory/loao/2023_0422/hdCalib-LOAO-NGC6946-20230423-114926-B-180.com.fits -CATALOG_NAME /data4/gecko/factory/loao/2023_0422/hdCalib-LOAO-NGC6946-20230423-114926-B-180.com.cat -CATALOG_TYPE ASCII_HEAD -PARAMETERS_NAME /home/paek/config/gregoryphot.param -DETECT_TYPE CCD -DETECT_MINAREA 10 -DETECT_MAXAREA 0 -DETECT_THRESH 1.25 -ANALYSIS_THRESH 1.5 -FILTER Y -FILTER_NAME /home/paek/config/gregoryphot.conv -DEBLEND_NTHRESH

> 
----- SExtractor 2.19.5 started on 2023-04-26 at 10:52:43 with 1 thread

> Setting catalog parameters
> Reading detection filter
> Initializing Neural Network
> Reading Neural Network Weights
> Initializing check-image(s)
> Initializing catalog
> Looking for hdCalib-LOAO-NGC6946-20230423-114926-B-180.com.fits
----- Measuring from: hdCalib-LOAO-NGC6946-20230423-114926-B-180.com.fits
      "NGC6946" / no ext. header / 2048x2048 / 32 bits (floats)
Detection+Measurement image: > Setting up background maps
> Setting up background map at line:   64
> Setting up background map at line:  128
> Setting up background map at line:  192
> Setting up background map at line:  256
> Setting up background map at line:  320
> Setting up background map at line:  384
> Setting up background map at line:  448
> Setting up background map at line:  512
> Setting up background map at line:  576
> Setting up background map at line:  640
> Setting up background map at line:  704
> Setting up background map 

ZERO POINT CALCULATION for MAG_AUTO
ZERO POINT CALCULATION for MAG_APER
ZERO POINT CALCULATION for MAG_APER_1
ZERO POINT CALCULATION for MAG_APER_2
ZERO POINT CALCULATION for MAG_APER_3
ZERO POINT CALCULATION for MAG_APER_4
ZERO POINT CALCULATION for MAG_APER_5
------------------------------------------------------------
[14/14] /data4/gecko/factory/loao/2023_0422/hdCalib-LOAO-NGC6946-20230423-115248-R-180.com.fits
LOAO	NGC6946 in R-band
------------------------------------------------------------
2. SOURCE EXTRACTOR
sex -c /home/paek/config/gregoryphot.sex /data4/gecko/factory/loao/2023_0422/hdCalib-LOAO-NGC6946-20230423-115248-R-180.com.fits -CATALOG_NAME /data4/gecko/factory/loao/2023_0422/hdCalib-LOAO-NGC6946-20230423-115248-R-180.com.cat -CATALOG_TYPE ASCII_HEAD -PARAMETERS_NAME /home/paek/config/gregoryphot.param -DETECT_TYPE CCD -DETECT_MINAREA 10 -DETECT_MAXAREA 0 -DETECT_THRESH 1.25 -ANALYSIS_THRESH 1.5 -FILTER Y -FILTER_NAME /home/paek/config/gregoryphot.conv -DEBLEND_NTHRESH

> 
----- SExtractor 2.19.5 started on 2023-04-26 at 10:52:44 with 1 thread

> Setting catalog parameters
> Reading detection filter
> Initializing Neural Network
> Reading Neural Network Weights
> Initializing check-image(s)
> Initializing catalog
> Looking for hdCalib-LOAO-NGC6946-20230423-115248-R-180.com.fits
----- Measuring from: hdCalib-LOAO-NGC6946-20230423-115248-R-180.com.fits
      "NGC6946" / no ext. header / 2048x2048 / 32 bits (floats)
Detection+Measurement image: > Setting up background maps
> Setting up background map at line:   64
> Setting up background map at line:  128
> Setting up background map at line:  192
> Setting up background map at line:  256
> Setting up background map at line:  320
> Setting up background map at line:  384
> Setting up background map at line:  448
> Setting up background map at line:  512
> Setting up background map at line:  576
> Setting up background map at line:  640
> Setting up background map at line:  704
> Setting up background map 

ZERO POINT CALCULATION for MAG_AUTO
ZERO POINT CALCULATION for MAG_APER
ZERO POINT CALCULATION for MAG_APER_1
ZERO POINT CALCULATION for MAG_APER_2
ZERO POINT CALCULATION for MAG_APER_3
ZERO POINT CALCULATION for MAG_APER_4
ZERO POINT CALCULATION for MAG_APER_5
5. RESULT TO FILES
0 failed images
PHOTOMETRY IS DONE.	(11.792 seconds)


##	Transient Search


In [26]:
st_ = time.time()
fovval = fov.value
#	Input table for transient search
tstbl = Table()
# hdimlist = sorted(glob.glob(f'{path_data}/hd*com.fits'))
hdimlist = sorted(glob.glob(f'{path_data}/hd*.fits'))
if len(hdimlist) != 0:
	tstbl['hdim'] = hdimlist
	tskeys = ['hdcat', 'hcim', 'inim', 'scicat', 'refim']
	for key in tskeys:
		tstbl[key] = ' '*300
	tstbl['fovval'] = fovval

	for i, hdim in enumerate(hdimlist):
		hdcat = hdim.replace('.fits','.phot_sub.cat')
		hcim = hdim.replace('hdCalib', 'hcCalib')
		inim = hdim.replace('hdCalib', 'Calib')
		scicat = inim.replace('.fits', '.phot.cat')

		hdr = fits.getheader(hdim)
		obj = hdr['object']
		filte = hdr['filter']
		path_refim = f'/data3/paek/factory/ref_frames/{obs}'
		refimlist = glob.glob(f'{path_refim}/Ref*{obj}*{filte}*.fits')
		refim = refimlist[0]


		for key, im in zip(tskeys, [hdcat, hcim, inim, scicat, refim]):
			tstbl[key][i] = im

	out_tstbl = f'{path_data}/transient_search.txt'
	tstbl.write(out_tstbl, format='ascii.tab', overwrite=True)

	com = f'python {path_find} {out_tstbl} {ncores}'
	print(com)
	subprocess.call(com, shell=True)		


protbl['status'][protbl['process']=='transient_search'] = True
protbl['time'][protbl['process']=='transient_search'] = int(time.time() - st_)

python ./phot/gregoryfind_bulk_mp_2021.py /data4/gecko/factory/loao/2023_0422/transient_search.txt 8
#	Transient Search Process
------------------------------------------------------------
14 images with 8 cores
------------------------------------------------------------
#	Input
------------------------------------------------------------
hdim : hdCalib-LOAO-NGC5850-20230423-110224-B-180.com.fits
hdcat : hdCalib-LOAO-NGC5850-20230423-110224-B-180.com.phot_sub.cat
hcim : hcCalib-LOAO-NGC5850-20230423-110224-B-180.com.fits
scicat : Calib-LOAO-NGC5850-20230423-110224-B-180.com.phot.cat
fovval : 28.1
------------------------------------------------------------
------------------------------------------------------------
#	Input
------------------------------------------------------------
hdim : hdCalib-LOAO-NGC6070-20230423-111940-B-180.com.fits
hdcat : hdCalib-LOAO-NGC6070-20230423-111940-B-180.com.phot_sub.cat
hcim : hcCalib-LOAO-NGC6070-20230423-111940-B-180.com.fits
scicat : Calib-LOA

> 
----- SExtractor 2.19.5 started on 2023-04-26 at 10:52:47 with 1 thread

> Setting catalog parameters
> Reading detection filter
> Initializing Neural Network
> Reading Neural Network Weights
> Initializing catalog
> Looking for invhdCalib-LOAO-NGC5850-20230423-110224-B-180.com.fits
----- Measuring from: invhdCalib-LOAO-NGC5850-20230423-110224-B-180.com.fits
      "NGC5850" / no ext. header / 2048x2048 / 32 bits (floats)
Detection+Measurement image: > Setting up background maps
> Setting up background map at line:  128
> Setting up background map at line:  256
> 
----- SExtractor 2.19.5 started on 2023-04-26 at 10:52:47 with 1 thread

> Setting catalog parameters
> Reading detection filter
> Initializing Neural Network
> Reading Neural Network Weights
> Initializing catalog
> Looking for invhdCalib-LOAO-NGC6090-20230423-104955-B-180.com.fits
----- Measuring from: invhdCalib-LOAO-NGC6090-20230423-104955-B-180.com.fits
      "NGC6090" / no ext. header / 2048x2048 / 32 bits (floats)
> 

sex -c /home/paek/config/transient.sex /data4/gecko/factory/loao/2023_0422/invhdCalib-LOAO-NGC6090-20230423-104955-B-180.com.fits -CATALOG_NAME /data4/gecko/factory/loao/2023_0422/invhdCalib-LOAO-NGC6090-20230423-104955-B-180.com.cat -CATALOG_TYPE ASCII_HEAD -PARAMETERS_NAME /home/paek/config/transient.param -DETECT_TYPE CCD -DETECT_MINAREA 5 -DETECT_MAXAREA 0 -DETECT_THRESH 1.5 -ANALYSIS_THRESH 1.5 -FILTER Y -FILTER_NAME /home/paek/config/transient.conv -DEBLEND_NTHRESH 64 -DEBLEND_MINCONT 0.0001 -CLEAN Y -CLEAN_PARAM 1.0 -MASK_TYPE CORRECT -PHOT_AUTOPARAMS 2.5,3.5 -PHOT_PETROPARAMS 2.0,3.5 -SATUR_LEVEL 65000.0 -SATUR_KEY SQTURATE -MAG_ZEROPOINT 0.0 -MAG_GAMMA 4.0 -GAIN 1.0 -GAIN_KEY GAIN -PIXEL_SCALE 1.0 -SEEING_FWHM 2.575 -STARNNW_NAME /home/paek/config/transient.nnw -BACK_SIZE 128 -BACK_FILTERSIZE 10 -BACKPHOTO_TYPE LOCAL -CHECKIMAGE_TYPE NONE -CHECKIMAGE_NAME check.fits -MEMORY_OBJSTACK 3000 -MEMORY_PIXSTACK 300000 -MEMORY_BUFSIZE 1024 -VERBOSE_TYPE NORMAL -HEADER_SUFFIX .head -WR

> Line:  775  Objects:      408 detected /        0 sextracted
> Line: 1250  Objects:      304 detected /       85 sextracted
> Line:  825  Objects:      555 detected /        0 sextracted
> Line: 1925  Objects:      128 detected /       65 sextracted
> Line:  800  Objects:      409 detected /        0 sextracted
> Line: 1950  Objects:      129 detected /       65 sextracted
> Line:  825  Objects:      410 detected /        0 sextracted
> Line:  850  Objects:      563 detected /        0 sextracted
> Line: 1975  Objects:      131 detected /       65 sextracted
> Line:  850  Objects:      411 detected /        0 sextracted
> Line: 2000  Objects:      133 detected /       65 sextracted
> Line:  875  Objects:      413 detected /        0 sextracted
      Objects: detected 166      / sextracted 152             

> Closing files
> 
> All done (in 0.2 s: 11443.6 lines/s , 849.3 detections/s)
> Line:  900  Objects:      416 detected /        0 sextracted
> Line: 2025  Objects:      137 detect

sex -c /home/paek/config/transient.sex /data4/gecko/factory/loao/2023_0422/invhcCalib-LOAO-NGC6090-20230423-105345-R-180.com.fits -CATALOG_NAME /data4/gecko/factory/loao/2023_0422/invhcCalib-LOAO-NGC6090-20230423-105345-R-180.com.cat -CATALOG_TYPE ASCII_HEAD -PARAMETERS_NAME /home/paek/config/transient.param -DETECT_TYPE CCD -DETECT_MINAREA 5 -DETECT_MAXAREA 0 -DETECT_THRESH 1.5 -ANALYSIS_THRESH 1.5 -FILTER Y -FILTER_NAME /home/paek/config/transient.conv -DEBLEND_NTHRESH 64 -DEBLEND_MINCONT 0.0001 -CLEAN Y -CLEAN_PARAM 1.0 -MASK_TYPE CORRECT -PHOT_AUTOPARAMS 2.5,3.5 -PHOT_PETROPARAMS 2.0,3.5 -SATUR_LEVEL 65000.0 -SATUR_KEY SQTURATE -MAG_ZEROPOINT 0.0 -MAG_GAMMA 4.0 -GAIN 1.0 -GAIN_KEY GAIN -PIXEL_SCALE 1.0 -SEEING_FWHM 2.533 -STARNNW_NAME /home/paek/config/transient.nnw -BACK_SIZE 128 -BACK_FILTERSIZE 10 -BACKPHOTO_TYPE LOCAL -CHECKIMAGE_TYPE NONE -CHECKIMAGE_NAME check.fits -MEMORY_OBJSTACK 3000 -MEMORY_PIXSTACK 300000 -MEMORY_BUFSIZE 1024 -VERBOSE_TYPE NORMAL -HEADER_SUFFIX .head -WR

...

No solar system object was found in the requested FOV (28.1 arcmin)


> Line: 1350  Objects:     4554 detected /      749 sextracted
> Line: 1375  Objects:     4611 detected /      793 sextracted
> Line: 1380  Objects:     4632 detected /      800 sextracted
> Line: 1400  Objects:     4698 detected /      825 sextracted
> Line: 1425  Objects:     4801 detected /      843 sextracted
> Line: 1450  Objects:     4872 detected /      857 sextracted
> Line: 1475  Objects:     4954 detected /      866 sextracted


flag==0 : 0 0%
flag==1 : 34 12%
flag==2 : 11 4%
flag==3 : 61 23%
flag==4 : 39 14%
flag==5 : 61 23%
flag==6 : 2 0%
flag==7 : 43 16%
flag==8 : 0 0%
flag==9 : 213 80%
flag==10 : 49 18%
flag==11 : 0 0%
flag==12 : 0 0%
------------------------------------------------------------
Filtered sources	: 248 93%
Transient Candidates	: 17 6%
#	Snapshot maker (17)


> Line: 1500  Objects:     4995 detected /      895 sextracted
> Line: 1525  Objects:     5116 detected /      929 sextracted
> Line: 1550  Objects:     5212 detected /      954 sextracted
> Line: 1575  Objects:     5473 detected /      993 sextracted
> Line: 1600  Objects:     5600 detected /     1036 sextracted
> Line: 1625  Objects:     5756 detected /     1088 sextracted
> Line: 1650  Objects:     5941 detected /     1139 sextracted
> Line: 1675  Objects:     6102 detected /     1194 sextracted
> Line: 1680  Objects:     6123 detected /     1200 sextracted
> Line: 1700  Objects:     6210 detected /     1229 sextracted
> Line: 1725  Objects:     6321 detected /     1270 sextracted
> Line: 1750  Objects:     6388 detected /     1308 sextracted
> Line: 1775  Objects:     6435 detected /     1341 sextracted
> Line: 1800  Objects:     6455 detected /     1341 sextracted
> Line: 1825  Objects:     6470 detected /     1341 sextracted
> Line: 1850  Objects:     6483 detected /     1341 sex

No solar system object was found in the requested FOV (28.1 arcmin)
flag==0 : 0 0%
flag==1 : 70 11%
flag==2 : 18 2%
flag==3 : 119 19%
flag==4 : 61 10%
flag==5 : 67 11%
flag==6 : 5 0%
flag==7 : 79 12%
flag==8 : 0 0%
flag==9 : 461 75%
flag==10 : 145 23%
flag==11 : 10 1%
flag==12 : 0 0%
------------------------------------------------------------
Filtered sources	: 523 85%
Transient Candidates	: 86 14%
#	Snapshot maker (86)


#	Summary file

In [27]:
#------------------------------------------------------------
#------------------------------------------------------------
protbl['status'][protbl['process']=='total'] = True
protbl['time'][protbl['process']=='total'] = int(time.time() - st)	
protbl.write('{}/obs.summary.log'.format(path_data), format='ascii.tab', overwrite=True)
print(protbl)
#	Write data summary
f = open(path_data+'/obs.summary.log', 'a')
end_localtime = time.strftime('%Y-%m-%d %H:%M:%S (%Z)', time.localtime())
f.write('Pipelne start\t: {}\n'.format(start_localtime))
f.write('Pipelne end\t: {}\n'.format(end_localtime))
try:
	f.write('='*60+'\n')
	f.write('PATH :{}\n'.format(path))
	f.write('OBJECT NUMBER # :{}\n'.format(len(ic_cal.summary)))
	objkind = sorted(set(ic_cal.summary['object']))
	f.write('OBJECTS # : {}\n'.format(objkind))
	for obj in objkind:
		f.write('-'*60+'\n')
		for filte in list(set(ic_cal.summary['filter'])):
			indx_tmp = ic_cal.files_filtered(filter=filte, object=obj)
			if len(indx_tmp) > 0:
				f.write('{}\t{}\n'.format(obj, filte))
except:
	pass
f.close()

    process      status  time
                          s  
---------------- ------ -----
    master_frame   True 141.0
     pre_process   True  48.0
      astrometry   True  27.0
      cr_removal   True  58.0
        defringe   True   0.0
      photometry   True  96.0
     image_stack   True  59.0
  photometry_com   True  47.0
     subtraction   True 233.0
  photometry_sub   True  13.0
transient_search   True 131.0
           total   True 826.0


## File Transfer

In [28]:
rmcom = 'rm {}/inv*.*'.format(path_data, path_data)
print(rmcom)
os.system(rmcom)
tails = ['.transients.', '.new.', '.ref.', '.sub.', '']
for obj in objlist:
	for filte in filterlist:
		for tail in tails:
			# tail = 'transients'
			# obj = 'NGC3147'
			# filte = 'B'

			pathto = f'{path_gal}/{obj}/{obs}/{filte}'
			files = f'{path_data}/*Calib*-{obj}-*-{filte}-*{tail}*'
			nfiles = len(glob.glob(files))
			# print(files, nfiles)
			# if nfiles >0:
			# 	print(obj, filte, pathto, files, glob.glob(files)[-1])
			if nfiles !=0:
				#	Save path
				if tail == '':
					pathto = f'{path_gal}/{obj}/{obs}/{filte}'
				else:
					pathto = f'{path_gal}/{obj}/{obs}/{filte}/transients'
				#	Make path
				if (not os.path.exists(pathto)):
					os.makedirs(pathto)
				mvcom = f'mv {files} {pathto}'
				print(mvcom)
				os.system(mvcom)
#	Image transfer
mvcom = f'mv {path_data} {path_save}'
os.system(mvcom)
#	WRITE LOG
f = open(path_log, 'a')
# f.write(path_raw+'/'+os.path.basename(path_data)+'\n')
# f.write('{}/{}\n'.format(path_raw, os.path.basename(path_data)))
f.write(f'{path_raw}/{os.path.basename(path_data)}\n')
f.close()

rm /data4/gecko/factory/loao/2023_0422/inv*.*
mv /data4/gecko/factory/loao/2023_0422/*Calib*-NGC5850-*-B-*.transients.* /data6/IMSNG/IMSNGgalaxies/NGC5850/LOAO/B/transients
mv /data4/gecko/factory/loao/2023_0422/*Calib*-NGC5850-*-B-*.new.* /data6/IMSNG/IMSNGgalaxies/NGC5850/LOAO/B/transients
mv /data4/gecko/factory/loao/2023_0422/*Calib*-NGC5850-*-B-*.ref.* /data6/IMSNG/IMSNGgalaxies/NGC5850/LOAO/B/transients
mv /data4/gecko/factory/loao/2023_0422/*Calib*-NGC5850-*-B-*.sub.* /data6/IMSNG/IMSNGgalaxies/NGC5850/LOAO/B/transients
mv /data4/gecko/factory/loao/2023_0422/*Calib*-NGC5850-*-B-** /data6/IMSNG/IMSNGgalaxies/NGC5850/LOAO/B
mv /data4/gecko/factory/loao/2023_0422/*Calib*-NGC5850-*-R-*.transients.* /data6/IMSNG/IMSNGgalaxies/NGC5850/LOAO/R/transients
mv /data4/gecko/factory/loao/2023_0422/*Calib*-NGC5850-*-R-*.new.* /data6/IMSNG/IMSNGgalaxies/NGC5850/LOAO/R/transients
mv /data4/gecko/factory/loao/2023_0422/*Calib*-NGC5850-*-R-*.ref.* /data6/IMSNG/IMSNGgalaxies/NGC5850/LOAO/R/transie

##	Slack message

In [29]:
total_time = round(protbl['time'][protbl['process']=='total'].item()/60., 1)

channel = '#pipeline'
text = f'[`gpPy`/{project}-{obsmode}] Processing Complete {obs} {os.path.basename(path)} Data ({nobj} objects) with {ncores} cores taking {total_time} mins'

param_slack = dict(
	token = OAuth_Token,
	channel = channel,
	text = text,
)

tool.slack_bot(**param_slack)

<Response [200]>
